# Capstone Project - The Neighborhoods of New York

### Applied Data Science Capstone by Shibbu Joseph

## Table of contents
* [Introduction](#introduction)
* [Data](#data)
* [Methodology](#methodology)
* [Analysis](#analysis)
* [Results and Discussion](#results)
* [Discussion](#discussion)
* [Conclusion](#conclusion)

## Introduction <a name="introduction"></a>

#### 1.1.	Background
 I chose to analyze New York City. It is the largest and most influential American metropolis. New York City is in reality a collection of many neighborhoods scattered among the city’s five boroughs: The Bronx, Brooklyn, Manhattan, Queens, and Staten Island, each exhibiting its own characteristics and ways of life. They say that moving from one neighborhood to another one may be like moving out to a different country. Therefore, it is advantageous to know how similar a neighborhood is to another one in each borough.
#### 1.2.	Problem
 This project aims to compare by similarity each neighborhood inside each borough, making clusters of neighborhoods, in order to learn which neighborhoods are similar, and which ones are substantially different. Having this information, I will also compare the results by analyzing the clusters distribution between each borough. Finally, I will give a general analysis of the complete New York City, comparing all the neighborhoods in the city.
#### 1.3.	Interest
 The following set of analyses may be useful to those moving to NYC, or moving from one neighborhood to another one within NYC. This would be especially helpful for those looking to move closer to an area with venues in their desired line of work. Real estate agents looking to improve their suggestions to clients may also find these analyses useful. In order to provide more tailored recommendations, real estate agents may use the venue information to match clients to areas that fit their desired job title and lifestyle.  

## Data <a name="data"></a>

#### 2.1.	Data sources
 The data was acquired through the city of New York Open Data team, published in the following site: https://opendata.cityofnewyork.us/. I selected the dataset named Neighborhood Names GIS. The raw data can be found in the following link: https://data.cityofnewyork.us/City-Government/Neighborhood-Names-GIS/99bc-9p23. The data contains the The_geom, object id, name, stacked, borough, Annoline1, Annoline2, Annoline3, AnnoAngle columns of each neighborhood. The_geom column contains the geolocation data, the borough is the name of the borough where the neighborhood belongs to, the Annolines columns are the names of the neighborhoods word by word and the stacked column is the amount of words in the neighborhood name. I will use this data to classify each of the neighborhoods. I will also use the foursquare API to retrieve a list of venues nearby each neighborhoods to make the analysis.


#### 2.2.	Data cleaning
 The data was downloaded but to work with the dataset I had to make a few changes in the dataset. First of all, I had to eliminate some columns that wouldn’t contribute at all with the analysis like stacked, Annoline1, Annoline2, Annoline3, and AnnoAngle, they information that this columns give are redundant for the analysis. After dropping each of these columns there was another problem: the_geom (the geolocation column) had a format of <POINT (Longitude, Latitude)>. To use this data point properly, we needed it in two columns: one for latitude and another one for longitude. To fix this data point I: 
1.	Eliminated all the POINT word and the parentheses of each data point.
2.	Separate the longitude and the latitude in different columns for each row.
3.	After doing all this the data frame was ready.
 Having cleaned the unnecessary parts of the data, I divided the data frame in six different frames, one for each borough and the final one for the whole list of neighborhoods in New York.
 I had to remove some neighborhoods in the data frame: One in Staten Island and one in New York called “Chelsea”. The first one didn’t have any nearby venues, so it couldn’t be compared to other neighborhoods. The second one was duplicated in the dataset, so I had to remove one instance.


First let´s import all the libraries that we will need.


In [1]:
import numpy as np # library to handle data in a vectorized manner
import pandas as pd # library for data analsysis
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import json # library to handle JSON files
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values
import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe
import matplotlib.cm as cm
import matplotlib.colors as colors
# import k-means from clustering stage
from sklearn.cluster import KMeans
import folium # map rendering library
print('Libraries imported.')

Libraries imported.


In [2]:
csv_path = 'https://data.cityofnewyork.us/api/views/xyye-rtrs/rows.csv?accessType=DOWNLOAD&bom=true&format=true'
nydf = pd.read_csv(csv_path)

In [3]:
nydf

the_geom  OBJECTID  \
0      POINT (-73.8472005205491 40.89470517661004)         1   
1     POINT (-73.82993910812405 40.87429419303015)         2   
2     POINT (-73.82780644716419 40.88755567735082)         3   
3    POINT (-73.90564259591689 40.895437426903875)         4   
4     POINT (-73.91258546108577 40.89083449389134)         5   
5     POINT (-73.90281798724611 40.88168737120525)         6   
6     POINT (-73.91065965862988 40.87655077879968)         7   
7    POINT (-73.86731496814183 40.898272612138086)         8   
8    POINT (-73.87939073956817 40.877224155994504)         9   
9     POINT (-73.85744642974214 40.88103887819214)        10   
10    POINT (-73.83579759808124 40.86685810725274)        11   
11    POINT (-73.85475564018006 40.85741349808869)        12   
12     POINT (-73.7864884526742 40.84724670491817)        13   
13    POINT (-73.88551218419137 40.87018516497537)        14   
14    POINT (-73.91041596191317 40.85572707719668)        15   
15    POINT (-73.91967159119572 40.84789792606274)        16   
16     POINT (-73.8964265598163 40.86099679638657)        17   
17    POINT (-73.88735617532345 40.84269615786057)        18   
18    POINT (-73.87774474910552 40.83947505672657)        19   
19     POINT (-73.92610209358138 40.8366230107061)        20   
20    POINT (-73.90942160757443 40.81975437059498)        21   
21    POINT (-73.91609987487583 40.80623874935181)        22   
22    POINT (-73.91322139386142 40.80166362775625)        23   
23   POINT (-73.89578820094466 40.815099045458254)        24   
24   POINT (-73.88331505955298 40.809729879387135)        25   
25    POINT (-73.90150648943066 40.82359198585537)        26   
26    POINT (-73.86574609554933 40.82101219791406)        27   
27   POINT (-73.85414416189273 40.806551120035934)        28   
28    POINT (-73.8163500215845 40.815109258040096)        29   
29    POINT (-73.82409926753857 40.84424593694742)        30   
30     POINT (-73.8560031053579 40.83793782226733)        31   
31    POINT (-73.8421940760445 40.840619496432744)        32   
32    POINT (-73.86629918075617 40.84360847124722)        33   
33    POINT (-73.85040178030428 40.84754906353638)        34   
34    POINT (-73.88845196134812 40.85727710073898)        35   
35       POINT (-73.917190482104 40.8813949772709)        36   
36     POINT (-73.90453054908934 40.9085428295067)        37   
37    POINT (-73.83207378240478 40.85064140940339)        38   
38    POINT (-73.82620275994081 40.82657951686926)        39   
39    POINT (-73.81388514428627 40.82198611816354)        40   
40    POINT (-73.84802729582742 40.81901437698835)        41   
41    POINT (-73.86332361652784 40.87137078192375)        42   
42    POINT (-73.8416119483123 40.862965624780024)        43   
43   POINT (-73.91558941773451 40.834283807338544)        44   
44    POINT (-73.85053524451942 40.82977429787165)        45   
45    POINT (-73.84808271877175 40.88456130303736)        46   
46    POINT (-74.03062069353821 40.62580106501069)        47   
47    POINT (-73.99517998380736 40.61100890202048)        48   
48    POINT (-74.01031618527792 40.64510294925433)        49   
49     POINT (-73.954240931274 40.730200984864744)        50   
50    POINT (-73.97347087708452 40.59526001306597)        51   
51   POINT (-73.96509448785343 40.576825065666085)        52   
52    POINT (-73.94318640482987 40.58689012678388)        53   
53    POINT (-73.95743840559946 40.61443251335102)        54   
54    POINT (-73.95840106533912 40.63632589026681)        55   
55     POINT (-73.9432911907359 40.67082917695298)        56   
56    POINT (-73.93610256185843 40.64171776668965)        57   
57    POINT (-73.98042110559481 40.64238195800357)        58   
58    POINT (-73.98007340430179 40.65694583575108)        59   
59    POINT (-73.96485924262697 40.67682226225477)        60   
60    POINT (-73.91023536176615 40.66394994339758)        61   
61    POINT (-73.95811529220936 40.70714439344255)        62   
62    POIN

In [4]:
nydf.drop(['OBJECTID','Stacked','AnnoLine1', 'AnnoLine2', 'AnnoLine3', 'AnnoAngle'], axis=1).head()

the_geom         Name Borough
0    POINT (-73.8472005205491 40.89470517661004)    Wakefield   Bronx
1   POINT (-73.82993910812405 40.87429419303015)   Co-op City   Bronx
2   POINT (-73.82780644716419 40.88755567735082)  Eastchester   Bronx
3  POINT (-73.90564259591689 40.895437426903875)    Fieldston   Bronx
4   POINT (-73.91258546108577 40.89083449389134)    Riverdale   Bronx

In [5]:
nydf = nydf[['Borough','Name','the_geom']]
nydf.head()

Borough         Name                                       the_geom
0   Bronx    Wakefield    POINT (-73.8472005205491 40.89470517661004)
1   Bronx   Co-op City   POINT (-73.82993910812405 40.87429419303015)
2   Bronx  Eastchester   POINT (-73.82780644716419 40.88755567735082)
3   Bronx    Fieldston  POINT (-73.90564259591689 40.895437426903875)
4   Bronx    Riverdale   POINT (-73.91258546108577 40.89083449389134)

In [6]:
nydf.dtypes

Borough     object
Name        object
the_geom    object
dtype: object

In [7]:
test = nydf
test.head()

Borough         Name                                       the_geom
0   Bronx    Wakefield    POINT (-73.8472005205491 40.89470517661004)
1   Bronx   Co-op City   POINT (-73.82993910812405 40.87429419303015)
2   Bronx  Eastchester   POINT (-73.82780644716419 40.88755567735082)
3   Bronx    Fieldston  POINT (-73.90564259591689 40.895437426903875)
4   Bronx    Riverdale   POINT (-73.91258546108577 40.89083449389134)

In [8]:
# start stop and step variables 
start, stop, step = 7, -1, 1

# converting to string data type 
test["the_geom"]= test["the_geom"].astype(str) 

# slicing till 2nd last element 
test["geolocation"]= test["the_geom"].str.slice(start, stop, step) 

# display 
test.head()

C:\Users\Shibbu\anaconda3\lib\site-packages\ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """
C:\Users\Shibbu\anaconda3\lib\site-packages\ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


Borough         Name                                       the_geom  \
0   Bronx    Wakefield    POINT (-73.8472005205491 40.89470517661004)   
1   Bronx   Co-op City   POINT (-73.82993910812405 40.87429419303015)   
2   Bronx  Eastchester   POINT (-73.82780644716419 40.88755567735082)   
3   Bronx    Fieldston  POINT (-73.90564259591689 40.895437426903875)   
4   Bronx    Riverdale   POINT (-73.91258546108577 40.89083449389134)   

                             geolocation  
0    -73.8472005205491 40.89470517661004  
1   -73.82993910812405 40.87429419303015  
2   -73.82780644716419 40.88755567735082  
3  -73.90564259591689 40.895437426903875  
4   -73.91258546108577 40.89083449389134

In [9]:
test.drop(['the_geom'], axis=1).head()

Borough         Name                            geolocation
0   Bronx    Wakefield    -73.8472005205491 40.89470517661004
1   Bronx   Co-op City   -73.82993910812405 40.87429419303015
2   Bronx  Eastchester   -73.82780644716419 40.88755567735082
3   Bronx    Fieldston  -73.90564259591689 40.895437426903875
4   Bronx    Riverdale   -73.91258546108577 40.89083449389134

In [10]:
# new data frame with split value columns 
new = test["geolocation"].str.split(" ", n = 1, expand = True) 
  
# making separate first name column from new data frame 
test["Longitude"]= new[0] 
  
# making separate last name column from new data frame 
test["Latitude"]= new[1] 
  
# Dropping old Name columns 
test.drop(columns =["geolocation"], inplace = True) 
  
# df display 
test.head()

C:\Users\Shibbu\anaconda3\lib\site-packages\ipykernel_launcher.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """
C:\Users\Shibbu\anaconda3\lib\site-packages\ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  
C:\Users\Shibbu\anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#return

Borough         Name                                       the_geom  \
0   Bronx    Wakefield    POINT (-73.8472005205491 40.89470517661004)   
1   Bronx   Co-op City   POINT (-73.82993910812405 40.87429419303015)   
2   Bronx  Eastchester   POINT (-73.82780644716419 40.88755567735082)   
3   Bronx    Fieldston  POINT (-73.90564259591689 40.895437426903875)   
4   Bronx    Riverdale   POINT (-73.91258546108577 40.89083449389134)   

            Longitude            Latitude  
0   -73.8472005205491   40.89470517661004  
1  -73.82993910812405   40.87429419303015  
2  -73.82780644716419   40.88755567735082  
3  -73.90564259591689  40.895437426903875  
4  -73.91258546108577   40.89083449389134

In [11]:
test.drop(columns =["the_geom"], inplace = True) 

C:\Users\Shibbu\anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


In [12]:
test.head()

Borough         Name           Longitude            Latitude
0   Bronx    Wakefield   -73.8472005205491   40.89470517661004
1   Bronx   Co-op City  -73.82993910812405   40.87429419303015
2   Bronx  Eastchester  -73.82780644716419   40.88755567735082
3   Bronx    Fieldston  -73.90564259591689  40.895437426903875
4   Bronx    Riverdale  -73.91258546108577   40.89083449389134

In [13]:
nydf = test

In [14]:
nydf.head()

Borough         Name           Longitude            Latitude
0   Bronx    Wakefield   -73.8472005205491   40.89470517661004
1   Bronx   Co-op City  -73.82993910812405   40.87429419303015
2   Bronx  Eastchester  -73.82780644716419   40.88755567735082
3   Bronx    Fieldston  -73.90564259591689  40.895437426903875
4   Bronx    Riverdale  -73.91258546108577   40.89083449389134

In [15]:
convert_dict = {'Latitude': float, 
                'Longitude': float
               } 
  
nydf = nydf.astype(convert_dict) 
print(nydf.dtypes) 

Borough       object
Name          object
Longitude    float64
Latitude     float64
dtype: object


In [16]:
nydf = nydf[['Borough','Name','Latitude','Longitude']]
nydf.head()

Borough         Name   Latitude  Longitude
0   Bronx    Wakefield  40.894705 -73.847201
1   Bronx   Co-op City  40.874294 -73.829939
2   Bronx  Eastchester  40.887556 -73.827806
3   Bronx    Fieldston  40.895437 -73.905643
4   Bronx    Riverdale  40.890834 -73.912585

In [17]:
nydf.sort_values(by=['Borough'], inplace = True)

Now lets create a dataframe for each borough

In [18]:
nydf.reset_index(inplace = True)

In [19]:
nydf.drop(columns =["index"], inplace = True) 

In [20]:
nydf.head()

Borough          Name   Latitude  Longitude
0   Bronx     Wakefield  40.894705 -73.847201
1   Bronx  Clason Point  40.806551 -73.854144
2   Bronx   Throgs Neck  40.815109 -73.816350
3   Bronx  Country Club  40.844246 -73.824099
4   Bronx   Parkchester  40.837938 -73.856003

Lets check the size

In [21]:
nydf.shape

(299, 4)

In [22]:
bronxdf, brooklyndf, manhdf, queendf, statisdf = nydf[:49], nydf[49:120], nydf[120:159], nydf[159:237], nydf[237:]

In [23]:
bronxdf.head()

Borough          Name   Latitude  Longitude
0   Bronx     Wakefield  40.894705 -73.847201
1   Bronx  Clason Point  40.806551 -73.854144
2   Bronx   Throgs Neck  40.815109 -73.816350
3   Bronx  Country Club  40.844246 -73.824099
4   Bronx   Parkchester  40.837938 -73.856003

In [24]:
brooklyndf.head()

Borough                 Name   Latitude  Longitude
49  Brooklyn    East Williamsburg  40.708492 -73.938858
50  Brooklyn         Spring Creek  40.657139 -73.869988
51  Brooklyn           Georgetown  40.623845 -73.916075
52  Brooklyn  Prospect Park South  40.647009 -73.962613
53  Brooklyn              Midwood  40.625596 -73.957595

In [25]:
manhdf.head()

Borough          Name   Latitude  Longitude
120  Manhattan      Flatiron  40.739673 -73.990947
121  Manhattan  Civic Center  40.715229 -74.005415
122  Manhattan    Tudor City  40.746917 -73.971219
123  Manhattan    Turtle Bay  40.752042 -73.967708
124  Manhattan  Sutton Place  40.760280 -73.963556

In [26]:
queendf.head()

Borough             Name   Latitude  Longitude
159  Queens  Queensboro Hill  40.744572 -73.825809
160  Queens       Somerville  40.597711 -73.796648
161  Queens    Rockaway Park  40.580343 -73.841534
162  Queens     Belle Harbor  40.576156 -73.854018
163  Queens      Lefrak City  40.736075 -73.862525

In [27]:
statisdf.head()

Borough              Name   Latitude  Longitude
237  Staten Island       Grymes Hill  40.624185 -74.087248
238  Staten Island         Todt Hill  40.597069 -74.111329
239  Staten Island       South Beach  40.580247 -74.079553
240  Staten Island     Port Richmond  40.633669 -74.129434
241  Staten Island  Mariner's Harbor  40.632546 -74.150085

Now lets drop the borough and reset the index in all of them

In [28]:
bronxdf.drop(columns =["Borough"], inplace = True) 
brooklyndf.drop(columns =["Borough"], inplace = True) 
manhdf.drop(columns =["Borough"], inplace = True) 
queendf.drop(columns =["Borough"], inplace = True) 
statisdf.drop(columns =["Borough"], inplace = True) 

C:\Users\Shibbu\anaconda3\lib\site-packages\pandas\core\frame.py:3997: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  errors=errors,


In [29]:
bronxdf.reset_index(inplace = True)
brooklyndf.reset_index(inplace = True)
manhdf.reset_index(inplace = True)
queendf.reset_index(inplace = True)
statisdf.reset_index(inplace = True)

Lets drop again the index column of all dataframes

In [30]:
bronxdf.drop(columns =["index"], inplace = True) 
brooklyndf.drop(columns =["index"], inplace = True) 
manhdf.drop(columns =["index"], inplace = True) 
queendf.drop(columns =["index"], inplace = True) 
statisdf.drop(columns =["index"], inplace = True) 

Lets check the size of our new dataframes

In [31]:
bronxdf.shape

(49, 3)

In [32]:
brooklyndf.shape

(71, 3)

In [33]:
manhdf.shape

(39, 3)

In [34]:
queendf.shape

(78, 3)

In [35]:
statisdf.shape

(62, 3)

## Methodology <a name="methodology"></a>

We will use the k-means method to cluster each of the neighborhoods. First, I used the foursquare API to obtain the venues. Having the list of venues, I applied an onehot coding procedure, that consist of putting in binary information the data we are analyzing, in which I classified what type of venues each were. Following this, I now had to group each venue in the list with the neighborhood it belonged to and with this, I was able to calculate in what frequency each type of venue appeared in each neighborhood. This frequency of each type of venue can be used to classify each neighborhoods top ten most common venues.
 Now that I have a data frame with the top type of venues in each neighborhood I was able to proceed to the clustering process. For this type of process the number of cluster will determine the number of different groups that each neighborhood will associate with. So for each borough I decide to create 5 cluster and for the full clustering of the neighborhoods of New York I decided to work with 8 cluster, the reason being is the amount of neighborhoods is much larger, and we can assume we will need more groups to classify the neighborhoods.
 Finally plotting in a map the k-means clustering we can show which neighborhoods and their top picks are in each cluster. The analysis of each cluster and look at their properties and comment which cluster is the most common to find in each borough and in New York.

## Analysis <a name="analysis"></a>

### Use geopy library to get the latitude and longitude values of New York City.

In [38]:
address = 'New York City, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of New York City are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of New York City are 40.7127281, -74.0060152.


## Create a map of New York with neighborhoods superimposed on top.

In [39]:
# create map of New York using latitude and longitude values
map_newyork = folium.Map(location=[latitude, longitude], zoom_start=10)

# add markers to map
for lat, lng, borough, name in zip(nydf['Latitude'], nydf['Longitude'], nydf['Borough'], nydf['Name']):
    label = '{}, {}'.format(name, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_newyork)  
    
map_newyork

## Now lets visualize each of the neighborhoods in each borough

## Bronx

Let's get the geographical coordinates of Bronx.

In [40]:
address = 'Bronx, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitudebx = location.latitude
longitudebx = location.longitude
print('The geograpical coordinate of Bronx are {}, {}.'.format(latitudebx, longitudebx))

The geograpical coordinate of Bronx are 40.8466508, -73.8785937.


Lets visualize it

In [41]:
# create map of Bronx using latitude and longitude values
map_bronx = folium.Map(location=[latitudebx, longitudebx], zoom_start=11)

# add markers to map
for lat, lng, label in zip(bronxdf['Latitude'], bronxdf['Longitude'], bronxdf['Name']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_bronx)  
    
map_bronx

##  Brooklyn

#### Let's get the geographical coordinates of Brooklyn.

In [42]:
address = 'Brooklyn, NY'

geolocator = Nominatim(user_agent="ny_explorer")
locationb = geolocator.geocode(address)
latitudeb = 40.6782 #location.latitude there is a problem with this adress so we put the input manually
longitudeb = -73.9442 #location.longitude there is a problem with this adress so we put the input manually
print('The geograpical coordinate of Brooklyn are {}, {}.'.format(latitudeb, longitudeb))

The geograpical coordinate of Brooklyn are 40.6782, -73.9442.


### Lets visualize it

In [44]:
# create map of Brooklyn using latitude and longitude values
map_brooklyn = folium.Map(location=[latitudeb, longitudeb], zoom_start=11)

# add markers to map
for lat, lng, label in zip(brooklyndf['Latitude'], brooklyndf['Longitude'], brooklyndf['Name']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_brooklyn)  
    
map_brooklyn

### Manhattan

Let's get the geographical coordinates of Manhattan

In [45]:
address = 'Manhattan, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitudem = location.latitude
longitudem = location.longitude
print('The geograpical coordinate of Manhattan are {}, {}.'.format(latitudem, longitudem))

The geograpical coordinate of Manhattan are 40.7896239, -73.9598939.


Lets visualize it

In [46]:
# create map of Manhattan using latitude and longitude values
map_manhattan = folium.Map(location=[latitudem, longitudem], zoom_start=11)

# add markers to map
for lat, lng, label in zip(manhdf['Latitude'], manhdf['Longitude'], manhdf['Name']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_manhattan)
    
map_manhattan

# Queens

Let's get the geographical coordinates of Queens.

In [47]:
address = 'Queens, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitudeq = location.latitude
longitudeq = location.longitude
print('The geograpical coordinate of Queens are {}, {}.'.format(latitudeq, longitudeq))

The geograpical coordinate of Queens are 40.7498243, -73.7976337.


Lets visualize it

In [48]:
# create map of Queens using latitude and longitude values
map_queens = folium.Map(location=[latitudeq, longitudeq], zoom_start=11)

# add markers to map
for lat, lng, label in zip(queendf['Latitude'], queendf['Longitude'], queendf['Name']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_queens)
    
map_queens

## Staten Island

Let's get the geographical coordinates of Staten Island.

In [49]:
address = 'Staten Island, NY'

geolocator = Nominatim(user_agent="ny_explorer")
location = geolocator.geocode(address)
latitudest = location.latitude
longitudest = location.longitude
print('The geograpical coordinate of Queens are {}, {}.'.format(latitudest, longitudest))

The geograpical coordinate of Queens are 40.5834557, -74.1496048.


Lets visualize it

In [50]:
# create map of Staten Island using latitude and longitude values
map_staten = folium.Map(location=[latitudest, longitudest], zoom_start=11)

# add markers to map
for lat, lng, label in zip(statisdf['Latitude'], statisdf['Longitude'], statisdf['Name']):
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_staten)
    
map_staten

### Next, we are going to start utilizing the Foursquare API to explore the neighborhoods and segment them.

### Define Foursquare Credentials and Version

In [52]:
CLIENT_ID = 'R0MQVGVY5FX4FIBLF0HH0GUL0CUAGGTG0YREDDWRI2MUCWTQ' # your Foursquare ID
CLIENT_SECRET = 'U3KDUDHPMX5PH0QYFHZOY0TLYUFENU4XULSYT5OD12BKZXSX' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version #20180605
LIMIT = 100

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: R0MQVGVY5FX4FIBLF0HH0GUL0CUAGGTG0YREDDWRI2MUCWTQ
CLIENT_SECRET:U3KDUDHPMX5PH0QYFHZOY0TLYUFENU4XULSYT5OD12BKZXSX


## Explore Neighborhoods in Bronx

In [53]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

LEts write the code to run the above function on each neighborhood and create a new dataframe called manhattan_venues

In [54]:
bronx_venues = getNearbyVenues(names=bronxdf['Name'],
                                   latitudes=bronxdf['Latitude'],
                                   longitudes=bronxdf['Longitude'],
                              )

Wakefield
Clason Point
Throgs Neck
Country Club
Parkchester
Westchester Square
Van Nest
Morris Park
Belmont
Spuyten Duyvil
North Riverdale
Soundview
Pelham Bay
Edgewater Park
Olinville
Pelham Gardens
Concourse
Unionport
Edenwald
Mount Hope
Mount Eden
Concourse Village
Claremont Village
Schuylerville
Morrisania
Castle Hill
Longwood
Co-op City
Hunts Point
Fieldston
Riverdale
Kingsbridge
Woodlawn
Norwood
Williamsbridge
Baychester
Pelham Parkway
Eastchester
Bedford Park
Melrose
High  Bridge
Mott Haven
West Farms
City Island
Fordham
Morris Heights
University Heights
East Tremont
Port Morris


### Let's check the size of the resulting dataframe

In [55]:
print(bronx_venues.shape)
bronx_venues.head()

(1130, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0    Wakefield              40.894705              -73.847201   
1    Wakefield              40.894705              -73.847201   
2    Wakefield              40.894705              -73.847201   
3    Wakefield              40.894705              -73.847201   
4    Wakefield              40.894705              -73.847201   

              Venue  Venue Latitude  Venue Longitude  Venue Category  
0  Lollipops Gelato       40.894123       -73.845892    Dessert Shop  
1          Rite Aid       40.896649       -73.844846        Pharmacy  
2  Carvel Ice Cream       40.890487       -73.848568  Ice Cream Shop  
3         Walgreens       40.896528       -73.844700        Pharmacy  
4            Subway       40.890468       -73.849152  Sandwich Place

In [56]:
bronx_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                               
Baychester                             21                      21     21   
Bedford Park                           35                      35     35   
Belmont                                97                      97     97   
Castle Hill                             8                       8      8   
City Island                            27                      27     27   
Claremont Village                      18                      18     18   
Clason Point                           10                      10     10   
Co-op City                             14                      14     14   
Concourse                              28                      28     28   
Concourse Village                      38                      38     38   
Country Club                            5                       5      5   
East Tremont                           19                      19     19   
Eastchester                            22                      22     22   
Edenwald                                4                       4      4   
Edgewater Park                         22                      22     22   
Fieldston                               4                       4      4   
Fordham                                82                      82     82   
High  Bridge                           25                      25     25   
Hunts Point                            12                      12     12   
Kingsbridge                            71                      71     71   
Longwood                                9                       9      9   
Melrose                                26                      26     26   
Morris Heights                          8                       8      8   
Morris Park                            23                      23     23   
Morrisania                             23                      23     23   
Mott Haven                             18                      18     18   
Mount Eden                             30                      30     30   
Mount Hope                             11                      11     11   
North Riverdale                        23                      23     23   
Norwood                                32                      32     32   
Olinville                               9                       9      9   
Parkchester                            32                      32     32   
Pelham Bay                             41                      41     41   
Pelham Gardens                         20                      20     20   
Pelham Parkway                         23                      23     23   
Port Morris                            12                      12     12   
Riverdale                              11                      11     11   
Schuylerville                          19                      19     19   
Soundview                              18                      18     18   
Spuyten Duyvil                         10                      10     10   
Throgs Neck                            11                      11     11   
Unionport                              21                      21     21   
University Heights                     22                      22     22   
Van Nest                               22                      22     22   
Wakefield                               9                       9      9   
West Farms                             23                      23     23   
Westchester Square                     33                      33     33   
Williamsbridge                          4                       4      4   
Woodlawn                               25                      25     25   

                    Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                         
Bay

Let's find out how many unique categories can be curated from all the returned venues

In [58]:
print('There are {} uniques categories.'.format(len(bronx_venues['Venue Category'].unique())))

There are 166 uniques categories.


### Analyze Each Neighborhood of Bronx

In [59]:
bronx_onehot = pd.get_dummies(bronx_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
bronx_onehot['Neighborhood'] = bronx_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [bronx_onehot.columns[-1]] + list(bronx_onehot.columns[:-1])
bronx_onehot = bronx_onehot[fixed_columns]

bronx_onehot.head()

Neighborhood  Accessories Store  African Restaurant  American Restaurant  \
0    Wakefield                  0                   0                    0   
1    Wakefield                  0                   0                    0   
2    Wakefield                  0                   0                    0   
3    Wakefield                  0                   0                    0   
4    Wakefield                  0                   0                    0   

   Arcade  Arepa Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0       0                 0            0           0                    0   
1       0                 0            0           0                    0   
2       0                 0            0           0                    0   
3       0                 0            0           0                    0   
4       0                 0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auto Workshop  BBQ Joint  Bagel Shop  \
0                 0                   0              0          0           0   
1                 0                   0              0          0           0   
2                 0                   0              0          0           0   
3                 0                   0              0          0           0   
4                 0                   0              0          0           0   

   Bakery  Bank  Bar  Baseball Field  Basketball Court  Beer Bar  Board Shop  \
0       0     0    0               0                 0         0           0   
1       0     0    0               0                 0         0           0   
2       0     0    0               0                 0         0           0   
3       0     0    0               0                 0         0           0   
4       0     0    0               0                 0         0           0   

   Boat or Ferry  Boutique  Bowling Alley  Breakfast Spot  Brewery  Buffet  \
0              0         0              0               0        0       0   
1              0         0              0               0        0       0   
2              0         0              0               0        0       0   
3              0         0              0               0        0       0   
4              0         0              0               0        0       0   

   Building  Burger Joint  Burrito Place  Bus Line  Bus Station  Bus Stop  \
0         0             0              0         0            0         0   
1         0             0              0         0            0         0   
2         0             0              0         0            0         0   
3         0             0              0         0            0         0   
4         0             0              0         0            0         0   

   Café  Candy Store  Caribbean Restaurant  Check Cashing Service  \
0     0            0                     0                      0   
1     0            0                     0                      0   
2     0            0                     0                      0   
3     0            0                     0                      0   
4     0            0                     0                      0   

   Cheese Shop  Chinese Restaurant  Clothing Store  Coffee Shop  \
0            0                   0               0            0   
1            0                   0               0            0   
2            0                   0               0            0   
3            0                   0               0            0   
4            0                   0               0            0   

   Comfort Food Restaurant  Construction & Landscaping  Convenience Store  \
0                        0                           0                  0   
1                        0                           0                  0   
2                        0                           0                  0   
3                        0                  

##### And let's examine the new dataframe size.

In [60]:
bronx_onehot.shape

(1130, 167)

### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [61]:
bronx_grouped = bronx_onehot.groupby('Neighborhood').mean().reset_index()
bronx_grouped

Neighborhood  Accessories Store  African Restaurant  \
0           Baychester           0.000000            0.000000   
1         Bedford Park           0.000000            0.000000   
2              Belmont           0.000000            0.000000   
3          Castle Hill           0.000000            0.000000   
4          City Island           0.000000            0.000000   
5    Claremont Village           0.000000            0.000000   
6         Clason Point           0.000000            0.000000   
7           Co-op City           0.000000            0.000000   
8            Concourse           0.000000            0.035714   
9    Concourse Village           0.000000            0.000000   
10        Country Club           0.000000            0.000000   
11        East Tremont           0.000000            0.000000   
12         Eastchester           0.000000            0.000000   
13            Edenwald           0.000000            0.000000   
14      Edgewater Park           0.000000            0.000000   
15           Fieldston           0.000000            0.000000   
16             Fordham           0.012195            0.012195   
17        High  Bridge           0.000000            0.000000   
18         Hunts Point           0.000000            0.000000   
19         Kingsbridge           0.000000            0.000000   
20            Longwood           0.000000            0.000000   
21             Melrose           0.000000            0.000000   
22      Morris Heights           0.000000            0.000000   
23         Morris Park           0.000000            0.000000   
24          Morrisania           0.000000            0.000000   
25          Mott Haven           0.000000            0.000000   
26          Mount Eden           0.000000            0.000000   
27          Mount Hope           0.000000            0.000000   
28     North Riverdale           0.000000            0.000000   
29             Norwood           0.000000            0.000000   
30           Olinville           0.000000            0.000000   
31         Parkchester           0.000000            0.000000   
32          Pelham Bay           0.000000            0.000000   
33      Pelham Gardens           0.000000            0.000000   
34      Pelham Parkway           0.000000            0.000000   
35         Port Morris           0.000000            0.000000   
36           Riverdale           0.000000            0.000000   
37       Schuylerville           0.000000            0.000000   
38           Soundview           0.000000            0.000000   
39      Spuyten Duyvil           0.000000            0.000000   
40         Throgs Neck           0.000000            0.000000   
41           Unionport           0.000000            0.000000   
42  University Heights           0.000000            0.045455   
43            Van Nest           0.000000            0.000000   
44           Wakefield           0.000000            0.000000   
45          West Farms           0.000000            0.000000   
46  Westchester Square           0.000000            0.000000   
47      Williamsbridge           0.000000            0.000000   
48            Woodlawn           0.000000            0.000000   

    American Restaurant    Arcade  Arepa Restaurant  Art Gallery  Art Museum  \
0              0.000000  0.047619          0.000000     0.000000    0.000000   
1              0.000000  0.000000          0.000000     0.000000    0.000000   
2              0.010309  0.000000          0.000000     0.000000    0.000000   
3              0.000000  0.000000          0.000000     0.000000    0.000000   
4              0.037037  0.000000          0.000000     0.000000    0.000000   
5              0.000000  0.000000          0.000000     0.000000    0.000000   
6              0.000000  0.000000          0.000000     0.000000    0.000000   
7              0.000000  0.000000          0.000000     0.000000    0.000000   
8              0.000000  0.000000      

### Lets check the size again

In [62]:
bronx_grouped.shape

(49, 167)

#### Let's print each neighborhood along with the top 5 most common venues

In [63]:
num_top_venues = 5

for hood in bronx_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = bronx_grouped[bronx_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Baychester----
                venue  freq
0          Donut Shop  0.10
1      Discount Store  0.05
2   Electronics Store  0.05
3  Spanish Restaurant  0.05
4           Pet Store  0.05


----Bedford Park----
                venue  freq
0               Diner  0.11
1  Mexican Restaurant  0.11
2  Chinese Restaurant  0.11
3         Pizza Place  0.09
4       Deli / Bodega  0.06


----Belmont----
                venue  freq
0  Italian Restaurant  0.19
1         Pizza Place  0.09
2       Deli / Bodega  0.07
3              Bakery  0.05
4       Grocery Store  0.03


----Castle Hill----
                       venue  freq
0                     Market  0.12
1                       Bank  0.12
2              Deli / Bodega  0.12
3                      Diner  0.12
4  Latin American Restaurant  0.12


----City Island----
                    venue  freq
0      Seafood Restaurant  0.07
1                    Park  0.07
2  Thrift / Vintage Store  0.07
3          Ice Cream Shop  0.04
4          Baseball Fi

4        Sandwich Place  0.11


----West Farms----
                   venue  freq
0            Bus Station  0.17
1               Bus Stop  0.09
2                   Park  0.09
3      Convenience Store  0.04
4  Outdoors & Recreation  0.04


----Westchester Square----
                  venue  freq
0  Fast Food Restaurant  0.09
1        Sandwich Place  0.06
2           Pizza Place  0.06
3              Pharmacy  0.06
4    Mexican Restaurant  0.06


----Williamsbridge----
                  venue  freq
0            Soup Place  0.25
1             Nightclub  0.25
2                   Bar  0.25
3  Caribbean Restaurant  0.25
4     Accessories Store  0.00


----Woodlawn----
           venue  freq
0            Pub  0.16
1  Deli / Bodega  0.12
2    Pizza Place  0.08
3     Playground  0.08
4            Bar  0.04




### Let's put that into a pandas dataframe

First, let's write a function to sort the venues in descending order.

In [64]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Now let's create the new dataframe and display the top 10 venues for each neighborhood.

In [65]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sortedBronx = pd.DataFrame(columns=columns)
neighborhoods_venues_sortedBronx['Neighborhood'] = bronx_grouped['Neighborhood']

for ind in np.arange(bronx_grouped.shape[0]):
    neighborhoods_venues_sortedBronx.iloc[ind, 1:] = return_most_common_venues(bronx_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sortedBronx.head()

Neighborhood      1st Most Common Venue 2nd Most Common Venue  \
0    Baychester                 Donut Shop  Fast Food Restaurant   
1  Bedford Park         Chinese Restaurant                 Diner   
2       Belmont         Italian Restaurant           Pizza Place   
3   Castle Hill  Latin American Restaurant           Pizza Place   
4   City Island         Seafood Restaurant                  Park   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                    Bank           Pizza Place             Pet Store   
1      Mexican Restaurant           Pizza Place         Deli / Bodega   
2           Deli / Bodega                Bakery          Dessert Shop   
3                Pharmacy         Deli / Bodega                 Diner   
4  Thrift / Vintage Store       Harbor / Marina    Italian Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0        Discount Store           Bus Station        Sandwich Place   
1        Sandwich Place           Supermarket                  Park   
2                  Bank         Grocery Store        Sandwich Place   
3                Market                  Bank           Bus Station   
4        Sandwich Place          Liquor Store                  Café   

  9th Most Common Venue 10th Most Common Venue  
0    Mexican Restaurant      Electronics Store  
1                   Pub            Bus Station  
2           Fish Market             Shoe Store  
3       Doctor's Office         Farmers Market  
4         Boat or Ferry             Smoke Shop

### Clustering of the neighborhoods of Bronx

#### Run k-means to cluster the neighborhood into 5 clusters. We will do this process with each borough

In [66]:
# set number of clusters
kclusters = 5

bronx_grouped_clustering = bronx_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(bronx_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 2, 2, 2, 2, 2, 1, 2, 2, 2])

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood

In [67]:
#neighborhoods_venues_sortedBronx.drop(['Cluster Labels'], axis = 1, inplace = True) #If you get the error that clusters are alredy inserted uncomment this.
#neighborhoods_venues_sortedBronx.head()

In [68]:
# add clustering labels
neighborhoods_venues_sortedBronx.insert(0, 'Cluster Labels', kmeans.labels_)

bronx_merged = bronxdf

# merge bronx_merged with bronxdf to add latitude/longitude for each neighborhood
bronx_merged = bronx_merged.join(neighborhoods_venues_sortedBronx.set_index('Neighborhood'), on='Name')

bronx_merged # check the last columns!

Name   Latitude  Longitude  Cluster Labels  \
0            Wakefield  40.894705 -73.847201               2   
1         Clason Point  40.806551 -73.854144               1   
2          Throgs Neck  40.815109 -73.816350               2   
3         Country Club  40.844246 -73.824099               3   
4          Parkchester  40.837938 -73.856003               2   
5   Westchester Square  40.840619 -73.842194               2   
6             Van Nest  40.843608 -73.866299               2   
7          Morris Park  40.847549 -73.850402               2   
8              Belmont  40.857277 -73.888452               2   
9       Spuyten Duyvil  40.881395 -73.917190               2   
10     North Riverdale  40.908543 -73.904531               2   
11           Soundview  40.821012 -73.865746               2   
12          Pelham Bay  40.850641 -73.832074               2   
13      Edgewater Park  40.821986 -73.813885               2   
14           Olinville  40.871371 -73.863324               0   
15      Pelham Gardens  40.862966 -73.841612               2   
16           Concourse  40.834284 -73.915589               2   
17           Unionport  40.829774 -73.850535               2   
18            Edenwald  40.884561 -73.848083               4   
19          Mount Hope  40.848842 -73.908299               2   
20          Mount Eden  40.843826 -73.916556               2   
21   Concourse Village  40.824780 -73.915847               2   
22   Claremont Village  40.831428 -73.901199               2   
23       Schuylerville  40.826580 -73.826203               2   
24          Morrisania  40.823592 -73.901506               2   
25         Castle Hill  40.819014 -73.848027               2   
26            Longwood  40.815099 -73.895788               2   
27          Co-op City  40.874294 -73.829939               2   
28         Hunts Point  40.809730 -73.883315               2   
29           Fieldston  40.895437 -73.905643               1   
30           Riverdale  40.890834 -73.912585               1   
31         Kingsbridge  40.881687 -73.902818               2   
32            Woodlawn  40.898273 -73.867315               2   
33             Norwood  40.877224 -73.879391               2   
34      Williamsbridge  40.881039 -73.857446               0   
35          Baychester  40.866858 -73.835798               2   
36      Pelham Parkway  40.857413 -73.854756               2   
37         Eastchester  40.887556 -73.827806               2   
38        Bedford Park  40.870185 -73.885512               2   
39             Melrose  40.819754 -73.909422               2   
40        High  Bridge  40.836623 -73.926102               2   
41          Mott Haven  40.806239 -73.916100               2   
42          West Farms  40.839475 -73.877745               2   
43         City Island  40.847247 -73.786488               2   
44             Fordham  40.860997 -73.896427               2   
45      Morris Heights  40.847898 -73.919672               2   
46  University Heights  40.855727 -73.910416               2   
47        East Tremont  40.842696 -73.887356               2   
48         Port Morris  40.801664 -73.913221               2   

        1st Most Common Venue      2nd Most Common Venue  \
0                    Pharmacy             Sandwich Place   
1                        Park                       Pool   
2          Italian Restaurant         Chinese Restaurant   
3              Sandwich Place                 Playground   
4                 Supermarket                Pizza Place   
5        Fast Food Restaurant             Sandwich Place   
6               Deli / Bodega                Pizza Place   
7                 Pizza Place                     Bakery   
8          Italian Restaurant                Pizza Place   
9                    Bus Line                   Pharmacy   
10                Pizza Place                       Bank   
11         Chinese Restaurant              Grocery Store   
12                       Bank       F

Let's visualize the resulting clusters

In [69]:
# create map
map_clustersBx = folium.Map(location=[latitudebx, longitudebx], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(bronx_merged['Latitude'], bronx_merged['Longitude'], bronx_merged['Name'], bronx_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clustersBx)
       
map_clustersBx

### Examine Clusters of Bronx

Now, we can examine each cluster and determine the discriminating venue categories that distinguish each cluster.

#### Cluster 1

In [71]:
bronx_merged.loc[bronx_merged['Cluster Labels'] == 0, bronx_merged.columns[[0] + list(range(4, bronx_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
14       Olinville  Caribbean Restaurant           Supermarket   
34  Williamsbridge                   Bar  Caribbean Restaurant   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
14           Pizza Place                  Food    Chinese Restaurant   
34             Nightclub            Soup Place         Women's Store   

   6th Most Common Venue 7th Most Common Venue   8th Most Common Venue  \
14         Deli / Bodega      Basketball Court  Furniture / Home Store   
34       Doctor's Office  Fast Food Restaurant          Farmers Market   

   9th Most Common Venue       10th Most Common Venue  
14         Women's Store            Electronics Store  
34     Electronics Store  Eastern European Restaurant

### Cluster 2

In [72]:
bronx_merged.loc[bronx_merged['Cluster Labels'] == 1, bronx_merged.columns[[0] + list(range(4, bronx_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
1   Clason Point                  Park                  Pool   
29     Fieldston                 Plaza           Bus Station   
30     Riverdale  Medical Supply Store                  Park   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
1          Grocery Store              Bus Stop         Boat or Ferry   
29  Medical Supply Store                 River     Electronics Store   
30           Bus Station                 Plaza                   Gym   

          6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
1     South American Restaurant     Convenience Store     Electronics Store   
29  Eastern European Restaurant             Drugstore            Donut Shop   
30                   Food Truck        Baseball Field                  Bank   

   9th Most Common Venue       10th Most Common Venue  
1              Drugstore                   Donut Shop  
29       Doctor's Office                     Dive Bar  
30              Dive Bar  Eastern European Restaurant

#### Cluster 3

In [73]:
bronx_merged.loc[bronx_merged['Cluster Labels'] == 2, bronx_merged.columns[[0] + list(range(4, bronx_merged.shape[1]))]]

Name      1st Most Common Venue      2nd Most Common Venue  \
0            Wakefield                   Pharmacy             Sandwich Place   
2          Throgs Neck         Italian Restaurant         Chinese Restaurant   
4          Parkchester                Supermarket                Pizza Place   
5   Westchester Square       Fast Food Restaurant             Sandwich Place   
6             Van Nest              Deli / Bodega                Pizza Place   
7          Morris Park                Pizza Place                     Bakery   
8              Belmont         Italian Restaurant                Pizza Place   
9       Spuyten Duyvil                   Bus Line                   Pharmacy   
10     North Riverdale                Pizza Place                       Bank   
11           Soundview         Chinese Restaurant              Grocery Store   
12          Pelham Bay                       Bank       Fast Food Restaurant   
13      Edgewater Park         Italian Restaurant                Coffee Shop   
15      Pelham Gardens                   Pharmacy                Bus Station   
16           Concourse              Grocery Store         Chinese Restaurant   
17           Unionport                 Donut Shop             Ice Cream Shop   
19          Mount Hope              Grocery Store         Mexican Restaurant   
20          Mount Eden                   Pharmacy                Supermarket   
21   Concourse Village             Sandwich Place         Mexican Restaurant   
22   Claremont Village              Grocery Store         Chinese Restaurant   
23       Schuylerville                       Bank                   Pharmacy   
24          Morrisania             Discount Store                 Donut Shop   
25         Castle Hill  Latin American Restaurant                Pizza Place   
26            Longwood              Grocery Store  Latin American Restaurant   
27          Co-op City       Fast Food Restaurant                Bus Station   
28         Hunts Point                       Food               Gourmet Shop   
31         Kingsbridge                Pizza Place                        Bar   
32            Woodlawn                        Pub              Deli / Bodega   
33             Norwood                Pizza Place                       Park   
35          Baychester                 Donut Shop       Fast Food Restaurant   
36      Pelham Parkway                Pizza Place              Deli / Bodega   
37         Eastchester       Caribbean Restaurant                Bus Station   
38        Bedford Park         Chinese Restaurant                      Diner   
39             Melrose                Pizza Place       Gym / Fitness Center   
40        High  Bridge                Pizza Place                   Pharmacy   
41          Mott Haven                Pizza Place                        Gym   
42          West Farms                Bus Station                   Bus Stop   
43         City Island         Seafood Restaurant                       Park   
44             Fordham          Mobile Phone Shop                 Shoe Store   
45      Morris Heights                       Bank                Pizza Place   
46  University Heights                Pizza Place        Fried Chicken Joint   
47        East Tremont                Pizza Place                 Restaurant   
48         Port Morris     Furniture / Home Store  Latin American Restaurant   

        3rd Most Common Venue 4th Most Common Venue  \
0              Ice Cream Shop         Deli / Bodega   
2                  Sports Bar             Juice Bar   
4                  Kids Store         Women's Store   
5                  Donut Shop              Pharmacy   
6                 Bus Station            Hookah Bar   
7               Deli / Bodega          Burger Joint   
8               Deli / Bodega                Bakery   
9                 Pizza Place         Grocery Store   
10         Chinese Restaurant    Italian Restaurant   
11                Pizza Pla

### Cluster 4

In [74]:
bronx_merged.loc[bronx_merged['Cluster Labels'] == 3, bronx_merged.columns[[0] + list(range(4, bronx_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
3  Country Club        Sandwich Place            Playground   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
3                   Spa    Athletics & Sports        Discount Store   

  6th Most Common Venue        7th Most Common Venue 8th Most Common Venue  \
3     Electronics Store  Eastern European Restaurant             Drugstore   

  9th Most Common Venue 10th Most Common Venue  
3            Donut Shop        Doctor's Office

### Cluster 5

In [75]:
bronx_merged.loc[bronx_merged['Cluster Labels'] == 4, bronx_merged.columns[[0] + list(range(4, bronx_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
18  Edenwald           Pizza Place         Grocery Store   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
18    Athletics & Sports           Supermarket         Women's Store   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
18            Distillery        Farmers Market     Electronics Store   

          9th Most Common Venue 10th Most Common Venue  
18  Eastern European Restaurant              Drugstore

Here we can see that there is a cluster that is more common that the other ones, In this specific cluster that is the number 3 in our k-means procedure, we can see that most of this venues are pizza places, bodegas or delis, banks and finally different kinds of restaurants but mostly Italian restaurants, there are other similitudes but most neighborhoods in the Bronx have this characteristics.

We can finally visualize the cluster of neighborhoods in Bronx, lets continue with Brooklyn

### Explore Neighborhoods in Brooklyn

In [76]:
brooklyn_venues = getNearbyVenues(names=brooklyndf['Name'],
                                   latitudes=brooklyndf['Latitude'],
                                   longitudes=brooklyndf['Longitude'],
                              )

East Williamsburg
Spring Creek
Georgetown
Prospect Park South
Midwood
North Side
Bergen Beach
City Line
Ocean Hill
Prospect Lefferts Gardens
Boerum Hill
Downtown
Sea Gate
South Side
Navy Yard
Rugby
Fort Hamilton
Clinton Hill
Homecrest
Dumbo
Broadway Junction
Weeksville
Vinegar Hill
Ocean Parkway
Fulton Ferry
Paerdegat Basin
New Lots
Remsen Village
Wingate
Ditmas Park
Highland Park
Mill Basin
Marine Park
Madison
Dyker Heights
Bensonhurst
Sunset Park
Bay Ridge
Williamsburg
Windsor Terrace
Kensington
East Flatbush
Crown Heights
Flatbush
Manhattan Terrace
Sheepshead Bay
Bushwick
Brighton Beach
Greenpoint
Gravesend
Prospect Heights
Brownsville
Bedford Stuyvesant
Brooklyn Heights
Borough Park
Bath Beach
Coney Island
Manhattan Beach
Mill Island
Flatlands
Canarsie
Gerritsen Beach
Starrett City
Cypress Hills
Park Slope
Fort Greene
Gowanus
Red Hook
Carroll Gardens
Cobble Hill
East New York


### Let's check the size of the resulting dataframe

In [77]:
print(brooklyn_venues.shape)
brooklyn_venues.head()

(2709, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  East Williamsburg              40.708492              -73.938858   
1  East Williamsburg              40.708492              -73.938858   
2  East Williamsburg              40.708492              -73.938858   
3  East Williamsburg              40.708492              -73.938858   
4  East Williamsburg              40.708492              -73.938858   

                Venue  Venue Latitude  Venue Longitude  \
0  Dun-Well Doughnuts       40.707429       -73.940260   
1           The Topaz       40.707327       -73.939754   
2        Champs Diner       40.708335       -73.940816   
3             Newtown       40.709153       -73.937147   
4           Tradesman       40.708192       -73.939960   

                  Venue Category  
0                     Donut Shop  
1                   Cocktail Bar  
2  Vegetarian / Vegan Restaurant  
3                           Café  
4                            Bar

In [78]:
brooklyn_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  \
Neighborhood                                                               
Bath Beach                                    52                      52   
Bay Ridge                                     80                      80   
Bedford Stuyvesant                            30                      30   
Bensonhurst                                   32                      32   
Bergen Beach                                   8                       8   
Boerum Hill                                  100                     100   
Borough Park                                  20                      20   
Brighton Beach                                43                      43   
Broadway Junction                             17                      17   
Brooklyn Heights                             100                     100   
Brownsville                                   15                      15   
Bushwick                                      66                      66   
Canarsie                                       6                       6   
Carroll Gardens                               51                      51   
City Line                                     34                      34   
Clinton Hill                                  95                      95   
Cobble Hill                                   95                      95   
Coney Island                                  16                      16   
Crown Heights                                 22                      22   
Cypress Hills                                 15                      15   
Ditmas Park                                   54                      54   
Downtown                                     100                     100   
Dumbo                                         63                      63   
Dyker Heights                                  5                       5   
East Flatbush                                  9                       9   
East New York                                 11                      11   
East Williamsburg                             65                      65   
Flatbush                                      25                      25   
Flatlands                                     17                      17   
Fort Greene                                   67                      67   
Fort Hamilton                                 62                      62   
Fulton Ferry                                  59                      59   
Georgetown                                    29                      29   
Gerritsen Beach                               19                      19   
Gowanus                                       62                      62   
Gravesend                                     27                      27   
Greenpoint                                   100                     100   
Highland Park                                 11                      11   
Homecrest                                     40                      40   
Kensington                                    36                      36   
Madison                                        9                       9   
Manhattan Beach                               11                      11   
Manhattan Terrace                             22                      22   
Marine Park                                   12                      12   
Midwood                                       12                      12   
Mill Basin                                    41                      41   
Mill Island                                    2                       2   
Navy Yard                                     30                      30   
New Lots                                      20                      20   
North Side                                   100                     100   
Ocean Hill                                    23                      23   

Let's find out how many unique categories can be curated from all the returned venues


In [79]:
print('There are {} uniques categories.'.format(len(brooklyn_venues['Venue Category'].unique())))

There are 289 uniques categories.


## Analyze Each Neighborhood Brooklyn

In [80]:
brooklyn_onehot = pd.get_dummies(brooklyn_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
brooklyn_onehot['Neighborhood'] = brooklyn_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [brooklyn_onehot.columns[-1]] + list(brooklyn_onehot.columns[:-1])
brooklyn_onehot = brooklyn_onehot[fixed_columns]

brooklyn_onehot.head()

Yoga Studio  Accessories Store  American Restaurant  Antique Shop  \
0            0                  0                    0             0   
1            0                  0                    0             0   
2            0                  0                    0             0   
3            0                  0                    0             0   
4            0                  0                    0             0   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Arts & Crafts Store  \
0                 0                       0            0                    0   
1                 0                       0            0                    0   
2                 0                       0            0                    0   
3                 0                       0            0                    0   
4                 0                       0            0                    0   

   Arts & Entertainment  Asian Restaurant  Athletics & Sports  BBQ Joint  \
0                     0                 0                   0          0   
1                     0                 0                   0          0   
2                     0                 0                   0          0   
3                     0                 0                   0          0   
4                     0                 0                   0          0   

   Bagel Shop  Bakery  Bank  Bar  Baseball Field  Baseball Stadium  \
0           0       0     0    0               0                 0   
1           0       0     0    0               0                 0   
2           0       0     0    0               0                 0   
3           0       0     0    0               0                 0   
4           0       0     0    1               0                 0   

   Basketball Court  Beach  Beer Bar  Beer Garden  Beer Store  Big Box Store  \
0                 0      0         0            0           0              0   
1                 0      0         0            0           0              0   
2                 0      0         0            0           0              0   
3                 0      0         0            0           0              0   
4                 0      0         0            0           0              0   

   Bike Rental / Bike Share  Bike Shop  Bistro  Board Shop  Boat or Ferry  \
0                         0          0       0           0              0   
1                         0          0       0           0              0   
2                         0          0       0           0              0   
3                         0          0       0           0              0   
4                         0          0       0           0              0   

   Bookstore  Boutique  Boxing Gym  Brazilian Restaurant  Breakfast Spot  \
0          0         0           0                     0               0   
1          0         0           0                     0               0   
2          0         0           0                     0               0   
3          0         0           0                     0               0   
4          0         0           0                     0               0   

   Brewery  Bridal Shop  Bridge  Bubble Tea Shop  Buffet  Burger Joint  \
0        0            0       0                0       0             0   
1        0            0       0                0       0             0   
2        0            0       0                0       0             0   
3        0            0       0                0       0             0   
4        0            0       0                0       0             0   

   Burmese Restaurant  Burrito Place  Bus Line  Bus Station  Bus Stop  \
0                   0              0         0            0         0   
1                   0              0         0            0         0   
2                   0              0         0            0         0   
3                   0              0         0            0        

And let's examine the new dataframe size.

In [81]:
brooklyn_onehot.shape

(2709, 289)

### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [82]:
brooklyn_grouped = brooklyn_onehot.groupby('Neighborhood').mean().reset_index()
brooklyn_grouped

Neighborhood  Yoga Studio  Accessories Store  \
0                  Bath Beach     0.000000           0.000000   
1                   Bay Ridge     0.000000           0.000000   
2          Bedford Stuyvesant     0.000000           0.000000   
3                 Bensonhurst     0.000000           0.000000   
4                Bergen Beach     0.000000           0.000000   
5                 Boerum Hill     0.020000           0.000000   
6                Borough Park     0.000000           0.000000   
7              Brighton Beach     0.000000           0.000000   
8           Broadway Junction     0.000000           0.000000   
9            Brooklyn Heights     0.040000           0.000000   
10                Brownsville     0.000000           0.000000   
11                   Bushwick     0.000000           0.000000   
12                   Canarsie     0.000000           0.000000   
13            Carroll Gardens     0.039216           0.000000   
14                  City Line     0.000000           0.000000   
15               Clinton Hill     0.031579           0.000000   
16                Cobble Hill     0.021053           0.000000   
17               Coney Island     0.000000           0.000000   
18              Crown Heights     0.000000           0.000000   
19              Cypress Hills     0.000000           0.000000   
20                Ditmas Park     0.018519           0.000000   
21                   Downtown     0.010000           0.000000   
22                      Dumbo     0.031746           0.000000   
23              Dyker Heights     0.000000           0.000000   
24              East Flatbush     0.000000           0.000000   
25              East New York     0.000000           0.000000   
26          East Williamsburg     0.000000           0.000000   
27                   Flatbush     0.000000           0.000000   
28                  Flatlands     0.000000           0.000000   
29                Fort Greene     0.014925           0.000000   
30              Fort Hamilton     0.000000           0.000000   
31               Fulton Ferry     0.000000           0.000000   
32                 Georgetown     0.000000           0.000000   
33            Gerritsen Beach     0.000000           0.000000   
34                    Gowanus     0.016129           0.000000   
35                  Gravesend     0.000000           0.000000   
36                 Greenpoint     0.030000           0.000000   
37              Highland Park     0.000000           0.000000   
38                  Homecrest     0.000000           0.000000   
39                 Kensington     0.000000           0.000000   
40                    Madison     0.000000           0.000000   
41            Manhattan Beach     0.000000           0.000000   
42          Manhattan Terrace     0.000000           0.000000   
43                Marine Park     0.000000           0.000000   
44                    Midwood     0.000000           0.000000   
45                 Mill Basin     0.000000           0.000000   
46                Mill Island     0.000000           0.000000   
47                  Navy Yard     0.000000           0.000000   
48                   New Lots     0.000000           0.000000   
49                 North Side     0.030000           0.000000   
50                 Ocean Hill     0.000000           0.000000   
51              Ocean Parkway     0.000000           0.000000   
52            Paerdegat Basin     0.000000           0.000000   
53                 Park Slope     0.015385           0.015385   
54           Prospect Heights     0.000000           0.000000   
55  Prospect Lefferts Gardens     0.000000           0.000000   
56        Prospect Park South     0.000000           0.000000   
57                   Red Hook     0.000000           0.000000   
58             Remsen Village     0.000000           0.000000   
59                      Rugby     0.000000           0.000000   
60                   Sea Gate     0.000000          

Lets check the size again

In [83]:
brooklyn_grouped.shape

(71, 289)

### Let's print each neighborhood along with the top 5 most common venues

In [84]:
num_top_venues = 5

for hood in brooklyn_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = brooklyn_grouped[brooklyn_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Bath Beach----
                venue  freq
0  Chinese Restaurant  0.12
1     Bubble Tea Shop  0.06
2         Gas Station  0.04
3        Dessert Shop  0.04
4          Donut Shop  0.04


----Bay Ridge----
                 venue  freq
0   Italian Restaurant  0.06
1                  Spa  0.06
2          Pizza Place  0.05
3           Bagel Shop  0.04
4  American Restaurant  0.04


----Bedford Stuyvesant----
           venue  freq
0    Coffee Shop  0.10
1           Café  0.07
2            Bar  0.07
3    Pizza Place  0.07
4  Deli / Bodega  0.07


----Bensonhurst----
                venue  freq
0        Dessert Shop  0.06
1      Ice Cream Shop  0.06
2    Sushi Restaurant  0.06
3          Donut Shop  0.06
4  Italian Restaurant  0.06


----Bergen Beach----
             venue  freq
0             Park  0.25
1  Harbor / Marina  0.25
2   Baseball Field  0.12
3       Playground  0.12
4     Hockey Field  0.12


----Boerum Hill----
                    venue  freq
0             Coffee Shop  0.07
1  

4  Paper / Office Supplies Store  0.06


----Paerdegat Basin----
                venue  freq
0    Asian Restaurant  0.25
1                Food  0.25
2    Business Service  0.25
3  Child Care Service  0.25
4        Optical Shop  0.00


----Park Slope----
                venue  freq
0         Coffee Shop  0.09
1        Burger Joint  0.06
2         Pizza Place  0.05
3  Italian Restaurant  0.05
4          Bagel Shop  0.05


----Prospect Heights----
                venue  freq
0                 Bar  0.09
1  Mexican Restaurant  0.06
2         Coffee Shop  0.04
3     Thai Restaurant  0.04
4        Cocktail Bar  0.04


----Prospect Lefferts Gardens----
                  venue  freq
0                Bakery  0.08
1                  Café  0.08
2  Caribbean Restaurant  0.06
3           Pizza Place  0.06
4         Deli / Bodega  0.06


----Prospect Park South----
                  venue  freq
0  Caribbean Restaurant  0.08
1              Pharmacy  0.06
2     Mobile Phone Shop  0.06
3         Grocery

### Let's put that into a pandas dataframe

Let's use the function to sort the venues in descending order and let's create the new dataframe and display the top 10 venues for each neighborhood.

In [85]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sortedBrook = pd.DataFrame(columns=columns)
neighborhoods_venues_sortedBrook['Neighborhood'] = brooklyn_grouped['Neighborhood']

for ind in np.arange(brooklyn_grouped.shape[0]):
    neighborhoods_venues_sortedBrook.iloc[ind, 1:] = return_most_common_venues(brooklyn_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sortedBrook.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0          Bath Beach    Chinese Restaurant       Bubble Tea Shop   
1           Bay Ridge    Italian Restaurant                   Spa   
2  Bedford Stuyvesant           Coffee Shop                  Café   
3         Bensonhurst            Donut Shop          Dessert Shop   
4        Bergen Beach                  Park       Harbor / Marina   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0           Video Store    Italian Restaurant           Gas Station   
1           Pizza Place            Bagel Shop   American Restaurant   
2           Pizza Place         Deli / Bodega                   Bar   
3        Ice Cream Shop      Sushi Restaurant    Italian Restaurant   
4          Hockey Field        Baseball Field            Playground   

  6th Most Common Venue 7th Most Common Venue    8th Most Common Venue  \
0           Pizza Place            Donut Shop     Fast Food Restaurant   
1      Greek Restaurant                   Bar               Playground   
2          Gourmet Shop              Tiki Bar  New American Restaurant   
3           Supermarket           Record Shop              Coffee Shop   
4    Athletics & Sports           Flea Market              Fish Market   

  9th Most Common Venue 10th Most Common Venue  
0          Dessert Shop               Pharmacy  
1        Sandwich Place                   Café  
2   Fried Chicken Joint               Boutique  
3                  Road           Liquor Store  
4     Fish & Chips Shop            Film Studio

### Clustering of the neighborhoods of Brooklyn

##### Run k-means to cluster the neighborhood into 5 clusters.

In [86]:
# set number of clusters
kclusters = 5

brooklyn_grouped_clustering = brooklyn_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(brooklyn_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([1, 1, 1, 1, 3, 1, 0, 1, 1, 1])

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [87]:
#neighborhoods_venues_sortedBrooklyn.drop(['Cluster Labels'], axis = 1, inplace = True) If you get the error that clusters are alredy inserted uncomment this.
#neighborhoods_venues_sortedBrooklyn.head()

In [88]:
# add clustering labels
neighborhoods_venues_sortedBrook.insert(0, 'Cluster Labels', kmeans.labels_)

brooklyn_merged = brooklyndf

# merge brooklyn_merged with broolyndf to add latitude/longitude for each neighborhood
brooklyn_merged = brooklyn_merged.join(neighborhoods_venues_sortedBrook.set_index('Neighborhood'), on='Name')

brooklyn_merged.head() # check the last columns!

Name   Latitude  Longitude  Cluster Labels  \
0    East Williamsburg  40.708492 -73.938858               1   
1         Spring Creek  40.657139 -73.869988               1   
2           Georgetown  40.623845 -73.916075               0   
3  Prospect Park South  40.647009 -73.962613               0   
4              Midwood  40.625596 -73.957595               0   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                   Bar                Bakery         Deli / Bodega   
1        Discount Store            Kids Store         Women's Store   
2                  Bank              Pharmacy        Breakfast Spot   
3  Caribbean Restaurant  Fast Food Restaurant           Pizza Place   
4           Pizza Place        Ice Cream Shop            Bagel Shop   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0          Cocktail Bar                  Café    Mexican Restaurant   
1             Pet Store         Shopping Mall          Burger Joint   
2            Donut Shop    Miscellaneous Shop   Japanese Restaurant   
3              Pharmacy     Mobile Phone Shop         Grocery Store   
4         Grocery Store     Convenience Store      Video Game Store   

  7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0        Sandwich Place          Concert Hall           Coffee Shop   
1            Shoe Store           Pizza Place     Mobile Phone Shop   
2        Shipping Store          Burger Joint    Mexican Restaurant   
3            Kids Store   Fried Chicken Joint    Mexican Restaurant   
4           Candy Store                Bakery              Pharmacy   

  10th Most Common Venue  
0   Gym / Fitness Center  
1            Supermarket  
2     Seafood Restaurant  
3       Department Store  
4                Factory

Let's visualize the resulting clusters

In [89]:
# create map
map_clustersBrook = folium.Map(location=[latitudeb, longitudeb], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(brooklyn_merged['Latitude'], brooklyn_merged['Longitude'], brooklyn_merged['Name'], brooklyn_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clustersBrook)
       
map_clustersBrook

### Examine Clusters of Brooklyn

Now, we can examine each cluster and determine the discriminating venue categories that distinguish each cluster.

### Cluster 1

In [90]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 0, brooklyn_merged.columns[[0] + list(range(4, brooklyn_merged.shape[1]))]]

Name      1st Most Common Venue      2nd Most Common Venue  \
2            Georgetown                       Bank                   Pharmacy   
3   Prospect Park South       Caribbean Restaurant       Fast Food Restaurant   
4               Midwood                Pizza Place             Ice Cream Shop   
7             City Line                 Donut Shop          Mobile Phone Shop   
15                Rugby       Caribbean Restaurant                       Bank   
18            Homecrest                       Bank                 Donut Shop   
26             New Lots         Salon / Barbershop                Pizza Place   
27       Remsen Village       Caribbean Restaurant       Fast Food Restaurant   
31           Mill Basin         Chinese Restaurant                Pizza Place   
36          Sunset Park  Latin American Restaurant         Mexican Restaurant   
42        Crown Heights                Pizza Place                       Café   
43             Flatbush         Mexican Restaurant                Coffee Shop   
44    Manhattan Terrace                Pizza Place              Deli / Bodega   
49            Gravesend                Pizza Place                     Lounge   
51          Brownsville              Moving Target        Fried Chicken Joint   
54         Borough Park                       Bank                Pizza Place   
59            Flatlands                   Pharmacy       Caribbean Restaurant   
62        Starrett City              Moving Target                Bus Station   
63        Cypress Hills                Pizza Place  Latin American Restaurant   
70        East New York       Fast Food Restaurant              Event Service   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
2         Breakfast Spot            Donut Shop    Miscellaneous Shop   
3            Pizza Place              Pharmacy     Mobile Phone Shop   
4             Bagel Shop         Grocery Store     Convenience Store   
7               Bus Stop   Fried Chicken Joint         Grocery Store   
15         Grocery Store            Restaurant     Mobile Phone Shop   
18         Grocery Store    Chinese Restaurant           Pizza Place   
26         Grocery Store   Fried Chicken Joint                 Plaza   
27        Sandwich Place           Gas Station           Salad Place   
31                   Gym   Japanese Restaurant              Pharmacy   
36                  Bank           Pizza Place                Bakery   
42                Museum                  Bank            Bagel Shop   
43  Caribbean Restaurant              Pharmacy                Bakery   
44        Ice Cream Shop            Donut Shop            Bagel Shop   
49                Bakery    Italian Restaurant   Sporting Goods Shop   
51    Chinese Restaurant                 Plaza            Playground   
54              Pharmacy  Fast Food Restaurant                  Café   
59   Fried Chicken Joint  Fast Food Restaurant    Chinese Restaurant   
62  Caribbean Restaurant         Shopping Mall            Donut Shop   
63         Metro Station         Women's Store        Ice Cream Shop   
70    Spanish Restaurant                 Plaza    Salon / Barbershop   

     6th Most Common Venue          7th Most Common Venue  \
2      Japanese Restaurant                 Shipping Store   
3            Grocery Store                     Kids Store   
4         Video Game Store                    Candy Store   
7      Sporting Goods Shop             Spanish Restaurant   
15      Salon / Barbershop                   Liquor Store   
18   Vietnamese Restaurant                 Sandwich Place   
26  Furniture / Home Store             Chinese Restaurant   
27                     Gym                     Donut Shop   
31                    Bank                   Liquor Store   
36                Pharmacy                            Gym   
42            Liquor Store                  Deli / Bodega   
43          Massage Studio                         Lounge   
44       Co

### Cluster 2

In [91]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 1, brooklyn_merged.columns[[0] + list(range(4, brooklyn_merged.shape[1]))]]

Name   1st Most Common Venue  \
0           East Williamsburg                     Bar   
1                Spring Creek          Discount Store   
5                  North Side             Coffee Shop   
8                  Ocean Hill           Deli / Bodega   
9   Prospect Lefferts Gardens                    Café   
10                Boerum Hill             Coffee Shop   
11                   Downtown             Coffee Shop   
12                   Sea Gate                     Spa   
13                 South Side                     Bar   
14                  Navy Yard             Film Studio   
16              Fort Hamilton             Pizza Place   
17               Clinton Hill             Pizza Place   
19                      Dumbo                    Park   
20          Broadway Junction              Donut Shop   
21                 Weeksville                Bus Line   
22               Vinegar Hill              Food Truck   
23              Ocean Parkway        Sushi Restaurant   
24               Fulton Ferry                    Park   
28                    Wingate     Fried Chicken Joint   
29                Ditmas Park      Chinese Restaurant   
30              Highland Park           Grocery Store   
33                    Madison              Bagel Shop   
34              Dyker Heights             Golf Course   
35                Bensonhurst              Donut Shop   
37                  Bay Ridge      Italian Restaurant   
38               Williamsburg             Pizza Place   
39            Windsor Terrace                   Diner   
40                 Kensington           Grocery Store   
45             Sheepshead Bay            Dessert Shop   
46                   Bushwick                     Bar   
47             Brighton Beach              Restaurant   
48                 Greenpoint                     Bar   
50           Prospect Heights                     Bar   
52         Bedford Stuyvesant             Coffee Shop   
53           Brooklyn Heights           Deli / Bodega   
55                 Bath Beach      Chinese Restaurant   
56               Coney Island        Baseball Stadium   
57            Manhattan Beach                Bus Stop   
60                   Canarsie        Asian Restaurant   
61            Gerritsen Beach                     Bar   
64                 Park Slope             Coffee Shop   
65                Fort Greene      Italian Restaurant   
66                    Gowanus  Furniture / Home Store   
67                   Red Hook      Seafood Restaurant   
68            Carroll Gardens                  Bakery   
69                Cobble Hill              Playground   

       2nd Most Common Venue        3rd Most Common Venue  \
0                     Bakery                Deli / Bodega   
1                 Kids Store                Women's Store   
5                Pizza Place                          Bar   
8              Grocery Store                       Bakery   
9                     Bakery                Deli / Bodega   
10                       Bar       Furniture / Home Store   
11              Burger Joint                  Pizza Place   
12       American Restaurant                  Bus Station   
13               Coffee Shop                  Pizza Place   
14               Coffee Shop           Mexican Restaurant   
16            Sandwich Place           Chinese Restaurant   
17        Italian Restaurant              Thai Restaurant   
19               Coffee Shop               Scenic Lookout   
20               Gas Station             Recording Studio   
21                Donut Shop           Chinese Restaurant   
22  Bike Rental / Bike Share                  Coffee Shop   
23               Pizza Place                   Bagel Shop   
24       American Restaurant                    Roof Deck   
28                    Bakery                Deli / Bodega   
29             Deli / Bodega             Department Store   
30             Deli / Bodega         Gym / Fitness Center   
33 

### Cluster 3

In [92]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 2, brooklyn_merged.columns[[0] + list(range(4, brooklyn_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
25  Paerdegat Basin    Child Care Service                  Food   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
25      Asian Restaurant      Business Service     Food & Drink Shop   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
25           Flower Shop           Flea Market           Fish Market   

   9th Most Common Venue 10th Most Common Venue  
25     Fish & Chips Shop          Event Service

### Cluster 4

In [93]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 3, brooklyn_merged.columns[[0] + list(range(4, brooklyn_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
6    Bergen Beach                  Park       Harbor / Marina   
32    Marine Park                   Gym         Deli / Bodega   
41  East Flatbush    Chinese Restaurant             Wine Shop   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
6           Hockey Field        Baseball Field            Playground   
32          Soccer Field           Pizza Place    Chinese Restaurant   
41      Department Store          Liquor Store                  Park   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
6     Athletics & Sports           Flea Market           Fish Market   
32                  Park      Basketball Court              Pharmacy   
41           Supermarket  Caribbean Restaurant              Pharmacy   

   9th Most Common Venue 10th Most Common Venue  
6      Fish & Chips Shop            Film Studio  
32    Athletics & Sports         Clothing Store  
41         Women's Store                   Farm

### Cluster 5

In [94]:
brooklyn_merged.loc[brooklyn_merged['Cluster Labels'] == 4, brooklyn_merged.columns[[0] + list(range(4, brooklyn_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
58  Mill Island                  Pool             Locksmith   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
58         Women's Store                 Field           Event Space   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
58               Factory    Falafel Restaurant                  Farm   

   9th Most Common Venue 10th Most Common Venue  
58        Farmers Market   Fast Food Restaurant

In the Brooklyn clusters we can see that there is a cluster that is more common that the other ones, In this specific cluster that is the number 4 in our k-means procedure, we can see that most of this venues are different kinds of restaurants, banks, grocery stores, actually there is a big variety of shops in this cluster, there are other similitudes but most neighborhoods in Brooklyn have this characteristics.

We can finally visualize the cluster of neighborhoods in Bronx, lets continue with Manhattan

### Explore Neighborhoods in Manhattan

In [96]:
manhattan_venues = getNearbyVenues(names=manhdf['Name'],
                                   latitudes=manhdf['Latitude'],
                                   longitudes=manhdf['Longitude'],
                              )

Flatiron
Civic Center
Tudor City
Turtle Bay
Sutton Place
Midtown South
Noho
Carnegie Hill
Stuyvesant Town
Marble Hill
West Village
Clinton
Upper East Side
East Harlem
Central Harlem
Manhattanville
Roosevelt Island
Upper West Side
Lincoln Square
Financial District
Midtown
Murray Hill
Hamilton Heights
Chelsea
Greenwich Village
East Village
Lower East Side
Tribeca
Inwood
Little Italy
Soho
Manhattan Valley
Morningside Heights
Gramercy
Washington Heights
Battery Park City
Chinatown
Lenox Hill
Yorkville


Let's check the size of the resulting dataframe

In [97]:
print(manhattan_venues.shape)
manhattan_venues.head()

(3149, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0     Flatiron              40.739673              -73.990947   
1     Flatiron              40.739673              -73.990947   
2     Flatiron              40.739673              -73.990947   
3     Flatiron              40.739673              -73.990947   
4     Flatiron              40.739673              -73.990947   

               Venue  Venue Latitude  Venue Longitude          Venue Category  
0         Fishs Eddy       40.738605       -73.990017  Furniture / Home Store  
1     SoulCycle 19th       40.739434       -73.992168            Cycle Studio  
2         sweetgreen       40.738061       -73.991223             Salad Place  
3  The Fhitting Room       40.739857       -73.993194                     Gym  
4     Five Iron Golf       40.738959       -73.991544             Sports Club

In [98]:
manhattan_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                
Battery Park City                       76                      76     76   
Carnegie Hill                           90                      90     90   
Central Harlem                          49                      49     49   
Chelsea                                100                     100    100   
Chinatown                              100                     100    100   
Civic Center                           100                     100    100   
Clinton                                100                     100    100   
East Harlem                             37                      37     37   
East Village                           100                     100    100   
Financial District                     100                     100    100   
Flatiron                               100                     100    100   
Gramercy                                90                      90     90   
Greenwich Village                      100                     100    100   
Hamilton Heights                        61                      61     61   
Inwood                                  57                      57     57   
Lenox Hill                             100                     100    100   
Lincoln Square                          94                      94     94   
Little Italy                           100                     100    100   
Lower East Side                         50                      50     50   
Manhattan Valley                        43                      43     43   
Manhattanville                          44                      44     44   
Marble Hill                             24                      24     24   
Midtown                                100                     100    100   
Midtown South                          100                     100    100   
Morningside Heights                     41                      41     41   
Murray Hill                            100                     100    100   
Noho                                   100                     100    100   
Roosevelt Island                        29                      29     29   
Soho                                   100                     100    100   
Stuyvesant Town                         21                      21     21   
Sutton Place                           100                     100    100   
Tribeca                                 85                      85     85   
Tudor City                              76                      76     76   
Turtle Bay                             100                     100    100   
Upper East Side                        100                     100    100   
Upper West Side                         98                      98     98   
Washington Heights                      84                      84     84   
West Village                           100                     100    100   
Yorkville                              100                     100    100   

                     Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                          
Battery Park City                76               76              76  
Carnegie Hill                    90               90              90  
Central Harlem                   49               49              49  
Chelsea                         100              100             100  
Chinatown                       100              100             100  
Civic Center                    100              100             100  
Clinton                         100              100             100  
East Harlem                      37               37              37  
East Village                    100              100             100  
Financial District              100              100             100  
Flatiron   

Let's find out how many unique categories can be curated from all the returned venues

In [99]:
print('There are {} uniques categories.'.format(len(manhattan_venues['Venue Category'].unique())))

There are 331 uniques categories.


### Analyze Each Neighborhood of Manhattan

In [100]:
manhattan_onehot = pd.get_dummies(manhattan_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
manhattan_onehot['Neighborhood'] = manhattan_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [manhattan_onehot.columns[-1]] + list(manhattan_onehot.columns[:-1])
manhattan_onehot = manhattan_onehot[fixed_columns]

manhattan_onehot.head()

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0     Flatiron                  0               0                  0   
1     Flatiron                  0               0                  0   
2     Flatiron                  0               0                  0   
3     Flatiron                  0               0                  0   
4     Flatiron                  0               0                  0   

   African Restaurant  American Restaurant  Antique Shop  Arepa Restaurant  \
0                   0                    0             0                 0   
1                   0                    0             0                 0   
2                   0                    0             0                 0   
3                   0                    0             0                 0   
4                   0                    0             0                 0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                       0            0           0                    0   
1                       0            0           0                    0   
2                       0            0           0                    0   
3                       0            0           0                    0   
4                       0            0           0                    0   

   Asian Restaurant  Athletics & Sports  Auditorium  Australian Restaurant  \
0                 0                   0           0                      0   
1                 0                   0           0                      0   
2                 0                   0           0                      0   
3                 0                   0           0                      0   
4                 0                   0           0                      0   

   Austrian Restaurant  Auto Workshop  BBQ Joint  Baby Store  Bagel Shop  \
0                    0              0          0           0           0   
1                    0              0          0           0           0   
2                    0              0          0           0           0   
3                    0              0          0           0           0   
4                    0              0          0           0           0   

   Bakery  Bank  Bar  Basketball Court  Beer Bar  Beer Garden  Beer Store  \
0       0     0    0                 0         0            0           0   
1       0     0    0                 0         0            0           0   
2       0     0    0                 0         0            0           0   
3       0     0    0                 0         0            0           0   
4       0     0    0                 0         0            0           0   

   Big Box Store  Bike Rental / Bike Share  Bike Shop  Bike Trail  Bistro  \
0              0                         0          0           0       0   
1              0                         0          0           0       0   
2              0                         0          0           0       0   
3              0                         0          0           0       0   
4              0                         0          0           0       0   

   Board Shop  Boat or Ferry  Bookstore  Boutique  Boxing Gym  \
0           0              0          0         0           0   
1           0              0          0         0           0   
2           0              0          0         0           0   
3           0              0          0         0           0   
4           0              0          0         0           0   

   Brazilian Restaurant  Breakfast Spot  Bridge  Bubble Tea Shop  Building  \
0                     0               0       0                0         0   
1                     0               0       0                0         0   
2                     0               0       0                0         0   
3                     0               0       0                0         0   
4               

And let's examine the new dataframe size.

In [101]:
manhattan_onehot.shape

(3149, 332)

### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [102]:
manhattan_grouped = manhattan_onehot.groupby('Neighborhood').mean().reset_index()
manhattan_grouped

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0     Battery Park City           0.000000        0.000000               0.00   
1         Carnegie Hill           0.000000        0.000000               0.00   
2        Central Harlem           0.000000        0.000000               0.00   
3               Chelsea           0.000000        0.000000               0.00   
4             Chinatown           0.000000        0.000000               0.00   
5          Civic Center           0.000000        0.000000               0.00   
6               Clinton           0.000000        0.000000               0.00   
7           East Harlem           0.000000        0.000000               0.00   
8          East Village           0.000000        0.000000               0.00   
9    Financial District           0.000000        0.000000               0.00   
10             Flatiron           0.000000        0.000000               0.00   
11             Gramercy           0.000000        0.000000               0.00   
12    Greenwich Village           0.010000        0.000000               0.00   
13     Hamilton Heights           0.000000        0.016393               0.00   
14               Inwood           0.000000        0.000000               0.00   
15           Lenox Hill           0.000000        0.000000               0.01   
16       Lincoln Square           0.000000        0.000000               0.00   
17         Little Italy           0.000000        0.000000               0.00   
18      Lower East Side           0.000000        0.000000               0.00   
19     Manhattan Valley           0.000000        0.000000               0.00   
20       Manhattanville           0.000000        0.000000               0.00   
21          Marble Hill           0.000000        0.000000               0.00   
22              Midtown           0.000000        0.000000               0.00   
23        Midtown South           0.000000        0.000000               0.00   
24  Morningside Heights           0.000000        0.000000               0.00   
25          Murray Hill           0.000000        0.000000               0.00   
26                 Noho           0.000000        0.000000               0.00   
27     Roosevelt Island           0.000000        0.000000               0.00   
28                 Soho           0.000000        0.000000               0.00   
29      Stuyvesant Town           0.000000        0.000000               0.00   
30         Sutton Place           0.000000        0.010000               0.00   
31              Tribeca           0.000000        0.000000               0.00   
32           Tudor City           0.000000        0.000000               0.00   
33           Turtle Bay           0.000000        0.000000               0.00   
34      Upper East Side           0.000000        0.000000               0.00   
35      Upper West Side           0.010204        0.000000               0.00   
36   Washington Heights           0.011905        0.000000               0.00   
37         West Village           0.010000        0.000000               0.00   
38            Yorkville           0.000000        0.000000               0.00   

    African Restaurant  American Restaurant  Antique Shop  Arepa Restaurant  \
0             0.000000             0.013158          0.00          0.000000   
1             0.000000             0.011111          0.00          0.000000   
2             0.061224             0.040816          0.00          0.000000   
3             0.000000             0.040000          0.00          0.000000   
4             0.000000             0.040000          0.00          0.000000   
5             0.000000             0.040000          0.01          0.000000   
6             0.000000             0.040000          0.00          0.000000   
7             0.000000             0.000000          0.00          0.000000   
8             0.000000             0.020000          0.00  

Lets check the size again

In [103]:
manhattan_grouped.shape

(39, 332)

Let's print each neighborhood along with the top 5 most common venues

In [104]:
num_top_venues = 5

for hood in manhattan_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = manhattan_grouped[manhattan_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Battery Park City----
            venue  freq
0            Park  0.07
1     Coffee Shop  0.07
2  Clothing Store  0.05
3             Gym  0.05
4           Hotel  0.05


----Carnegie Hill----
            venue  freq
0     Coffee Shop  0.08
1            Café  0.06
2       Wine Shop  0.04
3  Cosmetics Shop  0.04
4     Yoga Studio  0.03


----Central Harlem----
                  venue  freq
0    African Restaurant  0.06
1  Gym / Fitness Center  0.04
2           Art Gallery  0.04
3    Seafood Restaurant  0.04
4                   Bar  0.04


----Chelsea----
                 venue  freq
0          Coffee Shop  0.06
1               Bakery  0.05
2  American Restaurant  0.04
3                Hotel  0.03
4            Wine Shop  0.03


----Chinatown----
                 venue  freq
0   Chinese Restaurant  0.08
1               Bakery  0.07
2         Dessert Shop  0.04
3         Cocktail Bar  0.04
4  American Restaurant  0.04


----Civic Center----
                  venue  freq
0           Coffee

### Let's put that into a pandas dataframe

Let's use the function to sort the venues in descending order and let's create the new dataframe and display the top 10 venues for each neighborhood

In [105]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sortedManh = pd.DataFrame(columns=columns)
neighborhoods_venues_sortedManh['Neighborhood'] = manhattan_grouped['Neighborhood']

for ind in np.arange(manhattan_grouped.shape[0]):
    neighborhoods_venues_sortedManh.iloc[ind, 1:] = return_most_common_venues(manhattan_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sortedManh.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0  Battery Park City           Coffee Shop                  Park   
1      Carnegie Hill           Coffee Shop                  Café   
2     Central Harlem    African Restaurant    Chinese Restaurant   
3            Chelsea           Coffee Shop                Bakery   
4          Chinatown    Chinese Restaurant                Bakery   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0        Clothing Store                 Hotel                   Gym   
1             Wine Shop        Cosmetics Shop           Yoga Studio   
2   Fried Chicken Joint     French Restaurant   American Restaurant   
3   American Restaurant    Seafood Restaurant     French Restaurant   
4          Dessert Shop     Hotpot Restaurant          Cocktail Bar   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0         Memorial Site           Beer Garden         Boat or Ferry   
1             Bookstore    Italian Restaurant                   Bar   
2                   Bar    Seafood Restaurant           Art Gallery   
3           Art Gallery    Italian Restaurant        Ice Cream Shop   
4   American Restaurant    Salon / Barbershop                   Spa   

  9th Most Common Venue 10th Most Common Venue  
0          Gourmet Shop                  Plaza  
1           Pizza Place      French Restaurant  
2        Cosmetics Shop   Gym / Fitness Center  
3                 Hotel              Wine Shop  
4        Sandwich Place     Mexican Restaurant

### Clustering of the neighborhoods of Brooklyn

Run k-means to cluster the neighborhood into 5 clusters

In [106]:
# set number of clusters
kclusters = 5

manhattan_grouped_clustering = manhattan_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(manhattan_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([2, 1, 1, 1, 1, 2, 1, 0, 1, 2])

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [107]:
# add clustering labels
neighborhoods_venues_sortedManh.insert(0, 'Cluster Labels', kmeans.labels_)

manhattan_merged = manhdf

# merge manhattan_merged with manhdf to add latitude/longitude for each neighborhood
manhattan_merged = manhattan_merged.join(neighborhoods_venues_sortedManh.set_index('Neighborhood'), on='Name')

manhattan_merged.head() # check the last columns!

Name   Latitude  Longitude  Cluster Labels 1st Most Common Venue  \
0      Flatiron  40.739673 -73.990947               2   American Restaurant   
1  Civic Center  40.715229 -74.005415               2           Coffee Shop   
2    Tudor City  40.746917 -73.971219               0    Mexican Restaurant   
3    Turtle Bay  40.752042 -73.967708               1           Coffee Shop   
4  Sutton Place  40.760280 -73.963556               1                   Gym   

  2nd Most Common Venue 3rd Most Common Venue    4th Most Common Venue  \
0    Italian Restaurant   Japanese Restaurant  New American Restaurant   
1                 Hotel                   Spa             Cocktail Bar   
2                  Park                  Café                    Diner   
3    Italian Restaurant      Ramen Restaurant                    Hotel   
4  Gym / Fitness Center    Italian Restaurant              Pizza Place   

  5th Most Common Venue     6th Most Common Venue 7th Most Common Venue  \
0  Gym / Fitness Center  Mediterranean Restaurant           Coffee Shop   
1  Gym / Fitness Center       American Restaurant     French Restaurant   
2         Deli / Bodega          Greek Restaurant           Coffee Shop   
3      Sushi Restaurant       Japanese Restaurant    Seafood Restaurant   
4           Coffee Shop    Furniture / Home Store   American Restaurant   

  8th Most Common Venue 9th Most Common Venue 10th Most Common Venue  
0   Sporting Goods Shop                   Spa            Yoga Studio  
1           Yoga Studio                  Park                 Bakery  
2                Garden       Thai Restaurant     Seafood Restaurant  
3            Steakhouse         Deli / Bodega               Wine Bar  
4                  Park       Thai Restaurant                 Bakery

Let's visualize the resulting clusters


In [108]:
# create map
map_clustersManh = folium.Map(location=[latitudem, longitudem], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(manhattan_merged['Latitude'], manhattan_merged['Longitude'], manhattan_merged['Name'], manhattan_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clustersManh)
       
map_clustersManh

### Examine Clusters of Manhattan

Now, we can examine each cluster and determine the discriminating venue categories that distinguish each cluster

### Cluster 1

In [109]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 0, manhattan_merged.columns[[0] + list(range(4, manhattan_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
2            Tudor City    Mexican Restaurant                  Park   
13          East Harlem    Mexican Restaurant         Deli / Bodega   
15       Manhattanville           Coffee Shop    Seafood Restaurant   
22     Hamilton Heights           Pizza Place                  Café   
28               Inwood    Mexican Restaurant            Restaurant   
32  Morningside Heights                  Park   American Restaurant   
34   Washington Heights                  Café                Bakery   

   3rd Most Common Venue 4th Most Common Venue      5th Most Common Venue  \
2                   Café                 Diner              Deli / Bodega   
13        Sandwich Place                Bakery  Latin American Restaurant   
15    Chinese Restaurant         Deli / Bodega         Mexican Restaurant   
22           Coffee Shop         Deli / Bodega         Mexican Restaurant   
28                  Café                Lounge                   Wine Bar   
32           Coffee Shop             Bookstore               Burger Joint   
34     Mobile Phone Shop                  Bank  Latin American Restaurant   

   6th Most Common Venue    7th Most Common Venue 8th Most Common Venue  \
2       Greek Restaurant              Coffee Shop                Garden   
13            Steakhouse          Thai Restaurant            Restaurant   
15    Italian Restaurant         Sushi Restaurant          Burger Joint   
22           Yoga Studio           Sandwich Place                Bakery   
28         Deli / Bodega              Pizza Place                  Park   
32                  Café           Sandwich Place           Pizza Place   
34           Pizza Place  New American Restaurant            Donut Shop   

   9th Most Common Venue     10th Most Common Venue  
2        Thai Restaurant         Seafood Restaurant  
13                  Park                   Beer Bar  
15    Spanish Restaurant                   Boutique  
22                  Park  Latin American Restaurant  
28                Bakery       Caribbean Restaurant  
32                   Pub         Seafood Restaurant  
34    Spanish Restaurant           Tapas Restaurant

### Cluster 2

In [110]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 1, manhattan_merged.columns[[0] + list(range(4, manhattan_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
3          Turtle Bay           Coffee Shop    Italian Restaurant   
4        Sutton Place                   Gym  Gym / Fitness Center   
6                Noho    Italian Restaurant           Pizza Place   
7       Carnegie Hill           Coffee Shop                  Café   
9         Marble Hill        Discount Store           Coffee Shop   
10       West Village    Italian Restaurant   American Restaurant   
11            Clinton    Italian Restaurant               Theater   
12    Upper East Side               Exhibit           Coffee Shop   
14     Central Harlem    African Restaurant    Chinese Restaurant   
17    Upper West Side                   Bar                  Café   
18     Lincoln Square                 Plaza                  Café   
21        Murray Hill           Coffee Shop                 Hotel   
23            Chelsea           Coffee Shop                Bakery   
24  Greenwich Village    Italian Restaurant        Clothing Store   
25       East Village                   Bar          Cocktail Bar   
26    Lower East Side                  Café           Art Gallery   
29       Little Italy                Bakery                  Café   
30               Soho        Clothing Store              Boutique   
31   Manhattan Valley                   Bar    Mexican Restaurant   
33           Gramercy            Bagel Shop                   Bar   
36          Chinatown    Chinese Restaurant                Bakery   
37         Lenox Hill    Italian Restaurant           Coffee Shop   
38          Yorkville    Italian Restaurant                   Gym   

      3rd Most Common Venue  4th Most Common Venue     5th Most Common Venue  \
3          Ramen Restaurant                  Hotel          Sushi Restaurant   
4        Italian Restaurant            Pizza Place               Coffee Shop   
6         French Restaurant            Coffee Shop               Art Gallery   
7                 Wine Shop         Cosmetics Shop               Yoga Studio   
9            Sandwich Place                    Gym               Yoga Studio   
10  New American Restaurant                   Park              Cocktail Bar   
11                    Hotel   Gym / Fitness Center       American Restaurant   
12     Gym / Fitness Center     Italian Restaurant                    Bakery   
14      Fried Chicken Joint      French Restaurant       American Restaurant   
17       Italian Restaurant                 Bakery         Indian Restaurant   
18                  Theater  Performing Arts Venue              Concert Hall   
21                      Bar   Gym / Fitness Center       American Restaurant   
23      American Restaurant     Seafood Restaurant         French Restaurant   
24         Sushi Restaurant                   Café       American Restaurant   
25       Mexican Restaurant            Pizza Place                 Speakeasy   
26       Chinese Restaurant                 Bakery               Pizza Place   
29          Bubble Tea Shop           Cocktail Bar            Clothing Store   
30       Italian Restaurant            Coffee Shop  Mediterranean Restaurant   
31        Indian Restaurant            Coffee Shop               Pizza Place   
33       Italian Restaurant    American Restaurant               Coffee Shop   
36             Dessert Shop      Hotpot Restaurant              Cocktail Bar   
37             Cocktail Bar       Sushi Restaurant               Pizza Place   
38                      Bar            Coffee Shop             Deli / Bodega   

     6th Most Common Venue 7th Most Common Venue     8th Most Common Venue  \
3      Japanese Restaurant    Seafood Restaurant                Steakhouse   
4   Furniture / Home Store   American Restaurant                      Park   
6           Sandwich Place                Bakery        Mexican Restaurant   
7                Bookstore    Italian Restaurant                       Bar   
9           Tennis Stadium         Deli / Bodega 

### Cluster 3

In [111]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 2, manhattan_merged.columns[[0] + list(range(4, manhattan_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
0             Flatiron   American Restaurant    Italian Restaurant   
1         Civic Center           Coffee Shop                 Hotel   
5        Midtown South     Korean Restaurant                 Hotel   
19  Financial District           Coffee Shop                   Gym   
20             Midtown                 Hotel               Theater   
27             Tribeca    Italian Restaurant                  Park   
35   Battery Park City           Coffee Shop                  Park   

   3rd Most Common Venue    4th Most Common Venue 5th Most Common Venue  \
0    Japanese Restaurant  New American Restaurant  Gym / Fitness Center   
1                    Spa             Cocktail Bar  Gym / Fitness Center   
5              Hotel Bar      Japanese Restaurant        Cosmetics Shop   
19          Cocktail Bar      American Restaurant                   Bar   
20   Sporting Goods Shop              Coffee Shop        Clothing Store   
27   American Restaurant                      Spa              Wine Bar   
35        Clothing Store                    Hotel                   Gym   

       6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0   Mediterranean Restaurant           Coffee Shop   Sporting Goods Shop   
1        American Restaurant     French Restaurant           Yoga Studio   
5                Coffee Shop          Dessert Shop           Salad Place   
19               Pizza Place    Italian Restaurant  Gym / Fitness Center   
20                 Bookstore   American Restaurant            Steakhouse   
27               Coffee Shop                  Café                 Hotel   
35             Memorial Site           Beer Garden         Boat or Ferry   

   9th Most Common Venue 10th Most Common Venue  
0                    Spa            Yoga Studio  
1                   Park                 Bakery  
5    American Restaurant   Gym / Fitness Center  
19            Steakhouse            Salad Place  
20                Bakery         Sandwich Place  
27      Greek Restaurant                 Bakery  
35          Gourmet Shop                  Plaza

### Cluster 4

In [112]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 3, manhattan_merged.columns[[0] + list(range(4, manhattan_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
8  Stuyvesant Town                   Bar                  Park   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
8         Boat or Ferry           Coffee Shop           Pet Service   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
8              Fountain                Bistro  Gym / Fitness Center   

  9th Most Common Venue 10th Most Common Venue  
8        Farmers Market        Harbor / Marina

### Cluster 5

In [113]:
manhattan_merged.loc[manhattan_merged['Cluster Labels'] == 4, manhattan_merged.columns[[0] + list(range(4, manhattan_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
16  Roosevelt Island                  Park            Restaurant   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
16  Outdoors & Recreation  Gym / Fitness Center          Liquor Store   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
16          Soccer Field      Greek Restaurant           Coffee Shop   

   9th Most Common Venue 10th Most Common Venue  
16        Sandwich Place               Bus Line

The Manhattan cluster have a cluster that is more common that the other ones, In this specific cluster that is the number 2 in our k-means procedure, we can see that most of this venues are Italian, Korean, Japanese restaurants mostly Italian, coffee shops and gym or fitness centers, there are other similitudes but most neighborhoods in Manhattan have this characteristics.

We can finally visualize the cluster of neighborhoods in Manhattan, lets continue with Queens.

### Explore Neighborhoods in Queens

In [114]:
queens_venues = getNearbyVenues(names=queendf['Name'],
                                   latitudes=queendf['Latitude'],
                                   longitudes=queendf['Longitude'],
                              )

Queensboro Hill
Somerville
Rockaway Park
Belle Harbor
Lefrak City
Lindenwood
Ravenswood
Hillcrest
Brookville
Bellaire
Middle Village
Forest Hills Gardens
Jamaica Hills
Utopia
Pomonok
Astoria Heights
Hunters Point
Sunnyside Gardens
Blissville
Roxbury
Jamaica Estates
Malba
North Corona
Holliswood
Laurelton
Murray Hill
Whitestone
Bayside
Auburndale
Little Neck
Douglaston
Glen Oaks
Bellerose
Kew Gardens Hills
Fresh Meadows
Briarwood
Jamaica Center
Oakland Gardens
Queens Village
Floral Park
Hollis
College Point
South Ozone Park
Woodhaven
Rego Park
Astoria
Woodside
Jackson Heights
Elmhurst
Howard Beach
South Corona
Forest Hills
South Jamaica
Kew Gardens
Downtown Flushing
Long Island City
Sunnyside
East Elmhurst
Maspeth
Ridgewood
Glendale
Richmond Hill
St. Albans
Ozone Park
Rosedale
Neponsit
Rochdale
Springfield Gardens
Cambria Heights
Seaside
Arverne
Edgemere
Far Rockaway
Broad Channel
Breezy Point
Bay Terrace
Beechhurst
Steinway


Let's check the size of the resulting dataframe

In [115]:
print(queens_venues.shape)
queens_venues.head()

(2097, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Queensboro Hill              40.744572              -73.825809   
1  Queensboro Hill              40.744572              -73.825809   
2  Queensboro Hill              40.744572              -73.825809   
3  Queensboro Hill              40.744572              -73.825809   
4  Queensboro Hill              40.744572              -73.825809   

                                Venue  Venue Latitude  Venue Longitude  \
0               Kung Fu Xiao Long Bao       40.743380       -73.825741   
1                     Yeh's Bakery 紅葉       40.745714       -73.825912   
2               Tea Shop 168 & Bakery       40.743241       -73.825726   
3  Main Street Taiwanese Gourmet 北港台菜       40.743538       -73.825825   
4            Lake Pavilion Restaurant       40.742622       -73.824970   

        Venue Category  
0  Dumpling Restaurant  
1               Bakery  
2               Bakery  
3   Chinese Restaurant  
4   Chinese Restaurant

In [116]:
queens_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                 
Arverne                                  18                      18     18   
Astoria                                  99                      99     99   
Astoria Heights                          15                      15     15   
Auburndale                               15                      15     15   
Bay Terrace                              36                      36     36   
Bayside                                  77                      77     77   
Beechhurst                               16                      16     16   
Bellaire                                 12                      12     12   
Belle Harbor                             18                      18     18   
Bellerose                                19                      19     19   
Blissville                               18                      18     18   
Breezy Point                              6                       6      6   
Briarwood                                10                      10     10   
Broad Channel                             6                       6      6   
Brookville                                1                       1      1   
Cambria Heights                          13                      13     13   
College Point                            40                      40     40   
Douglaston                               22                      22     22   
Downtown Flushing                       100                     100    100   
East Elmhurst                            11                      11     11   
Edgemere                                 14                      14     14   
Elmhurst                                 32                      32     32   
Far Rockaway                             30                      30     30   
Floral Park                               8                       8      8   
Forest Hills                             41                      41     41   
Forest Hills Gardens                     23                      23     23   
Fresh Meadows                            14                      14     14   
Glen Oaks                                20                      20     20   
Glendale                                  5                       5      5   
Hillcrest                                18                      18     18   
Hollis                                   14                      14     14   
Holliswood                                6                       6      6   
Howard Beach                             38                      38     38   
Hunters Point                            68                      68     68   
Jackson Heights                          79                      79     79   
Jamaica Center                           47                      47     47   
Jamaica Estates                           3                       3      3   
Jamaica Hills                            26                      26     26   
Kew Gardens                              48                      48     48   
Kew Gardens Hills                        19                      19     19   
Laurelton                                 5                       5      5   
Lefrak City                              20                      20     20   
Lindenwood                               13                      13     13   
Little Neck                              51                      51     51   
Long Island City                         70                      70     70   
Malba                                     3                       3      3   
Maspeth                                  32                      32     32   
Middle Village                           16                      16     16   
Murray Hill                              47                      47     47   
Neponsit                                  6 

Let's find out how many unique categories can be curated from all the returned venues

In [117]:
print('There are {} uniques categories.'.format(len(queens_venues['Venue Category'].unique())))

There are 267 uniques categories.


## Analyze Each Neighborhood of Queens

In [118]:
queens_onehot = pd.get_dummies(queens_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
queens_onehot['Neighborhood'] = queens_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [queens_onehot.columns[-1]] + list(queens_onehot.columns[:-1])
queens_onehot = queens_onehot[fixed_columns]

queens_onehot.head()

Yoga Studio  Accessories Store  Afghan Restaurant  American Restaurant  \
0            0                  0                  0                    0   
1            0                  0                  0                    0   
2            0                  0                  0                    0   
3            0                  0                  0                    0   
4            0                  0                  0                    0   

   Antique Shop  Arepa Restaurant  Argentinian Restaurant  Art Gallery  \
0             0                 0                       0            0   
1             0                 0                       0            0   
2             0                 0                       0            0   
3             0                 0                       0            0   
4             0                 0                       0            0   

   Art Museum  Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0           0                    0                     0                 0   
1           0                    0                     0                 0   
2           0                    0                     0                 0   
3           0                    0                     0                 0   
4           0                    0                     0                 0   

   Athletics & Sports  Automotive Shop  BBQ Joint  Bagel Shop  Bakery  Bank  \
0                   0                0          0           0       0     0   
1                   0                0          0           0       1     0   
2                   0                0          0           0       1     0   
3                   0                0          0           0       0     0   
4                   0                0          0           0       0     0   

   Bar  Baseball Field  Basketball Court  Bath House  Beach  Beach Bar  \
0    0               0                 0           0      0          0   
1    0               0                 0           0      0          0   
2    0               0                 0           0      0          0   
3    0               0                 0           0      0          0   
4    0               0                 0           0      0          0   

   Beer Garden  Bike Trail  Bistro  Board Shop  Bookstore  Boutique  \
0            0           0       0           0          0         0   
1            0           0       0           0          0         0   
2            0           0       0           0          0         0   
3            0           0       0           0          0         0   
4            0           0       0           0          0         0   

   Bowling Alley  Boxing Gym  Brazilian Restaurant  Breakfast Spot  Brewery  \
0              0           0                     0               0        0   
1              0           0                     0               0        0   
2              0           0                     0               0        0   
3              0           0                     0               0        0   
4              0           0                     0               0        0   

   Bubble Tea Shop  Buffet  Burger Joint  Burrito Place  Bus Station  \
0                0       0             0              0            0   
1                0       0             0              0            0   
2                0       0             0              0            0   
3                0       0             0              0            0   
4                0       0             0              0            0   

   Bus Stop  Business Service  Butcher  Café  Cajun / Creole Restaurant  \
0         0                 0        0     0                          0   
1         0                 0        0     0                          0   
2         0                 0        0     0                          0   
3         0                 0        0     0                          0

And let's examine the new dataframe size.

In [119]:
manhattan_onehot.shape

(3149, 332)

### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [120]:
queens_grouped = queens_onehot.groupby('Neighborhood').mean().reset_index()
queens_grouped

Neighborhood  Yoga Studio  Accessories Store  Afghan Restaurant  \
0                Arverne     0.000000           0.000000           0.000000   
1                Astoria     0.000000           0.000000           0.000000   
2        Astoria Heights     0.000000           0.000000           0.000000   
3             Auburndale     0.000000           0.000000           0.000000   
4            Bay Terrace     0.000000           0.027778           0.000000   
5                Bayside     0.012987           0.000000           0.000000   
6             Beechhurst     0.000000           0.000000           0.000000   
7               Bellaire     0.000000           0.000000           0.000000   
8           Belle Harbor     0.000000           0.000000           0.000000   
9              Bellerose     0.000000           0.000000           0.000000   
10            Blissville     0.000000           0.000000           0.000000   
11          Breezy Point     0.000000           0.000000           0.000000   
12             Briarwood     0.000000           0.000000           0.000000   
13         Broad Channel     0.000000           0.000000           0.000000   
14            Brookville     0.000000           0.000000           0.000000   
15       Cambria Heights     0.000000           0.000000           0.000000   
16         College Point     0.000000           0.000000           0.000000   
17            Douglaston     0.000000           0.000000           0.000000   
18     Downtown Flushing     0.000000           0.000000           0.000000   
19         East Elmhurst     0.000000           0.000000           0.000000   
20              Edgemere     0.000000           0.000000           0.000000   
21              Elmhurst     0.000000           0.000000           0.000000   
22          Far Rockaway     0.000000           0.000000           0.000000   
23           Floral Park     0.000000           0.000000           0.000000   
24          Forest Hills     0.048780           0.000000           0.000000   
25  Forest Hills Gardens     0.000000           0.000000           0.000000   
26         Fresh Meadows     0.000000           0.000000           0.000000   
27             Glen Oaks     0.000000           0.000000           0.000000   
28              Glendale     0.000000           0.000000           0.000000   
29             Hillcrest     0.000000           0.000000           0.000000   
30                Hollis     0.000000           0.000000           0.000000   
31            Holliswood     0.000000           0.000000           0.000000   
32          Howard Beach     0.000000           0.000000           0.000000   
33         Hunters Point     0.014706           0.000000           0.000000   
34       Jackson Heights     0.000000           0.000000           0.000000   
35        Jamaica Center     0.000000           0.000000           0.000000   
36       Jamaica Estates     0.000000           0.000000           0.000000   
37         Jamaica Hills     0.000000           0.000000           0.000000   
38           Kew Gardens     0.000000           0.000000           0.000000   
39     Kew Gardens Hills     0.000000           0.000000           0.000000   
40             Laurelton     0.000000           0.000000           0.000000   
41           Lefrak City     0.000000           0.000000           0.000000   
42            Lindenwood     0.000000           0.000000           0.000000   
43           Little Neck     0.000000           0.000000           0.000000   
44      Long Island City     0.000000           0.000000           0.000000   
45                 Malba     0.000000           0.000000           0.000000   
46               Maspeth     0.000000           0.000000           0.000000   
47        Middle Village     0.000000           0.000000           0.000000   
48           Murray Hill     0.000000           0.000000           0.000000   
49              Neponsit     0.000000           0.000000      

Lets check the size again

In [121]:
queens_grouped.shape

(78, 267)

Let's print each neighborhood along with the top 5 most common venues

In [122]:
num_top_venues = 5

for hood in queens_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = queens_grouped[queens_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Arverne----
           venue  freq
0      Surf Spot  0.22
1  Metro Station  0.11
2    Pizza Place  0.06
3          Beach  0.06
4       Bus Stop  0.06


----Astoria----
                       venue  freq
0                        Bar  0.07
1  Middle Eastern Restaurant  0.06
2           Greek Restaurant  0.04
3                       Café  0.04
4         Seafood Restaurant  0.04


----Astoria Heights----
           venue  freq
0  Deli / Bodega  0.07
1         Bakery  0.07
2         Hostel  0.07
3   Gourmet Shop  0.07
4          Motel  0.07


----Auburndale----
                venue  freq
0  Athletics & Sports  0.07
1        Noodle House  0.07
2         Supermarket  0.07
3  Miscellaneous Shop  0.07
4    Toy / Game Store  0.07


----Bay Terrace----
               venue  freq
0     Clothing Store  0.11
1         Kids Store  0.06
2  Mobile Phone Shop  0.06
3               Bank  0.06
4      Women's Store  0.06


----Bayside----
               venue  freq
0                Bar  0.08
1  Indian

4              Bakery  0.04


----Long Island City----
                  venue  freq
0                 Hotel  0.11
1           Coffee Shop  0.10
2  Gym / Fitness Center  0.06
3           Pizza Place  0.06
4                   Bar  0.06


----Malba----
          venue  freq
0     Rock Club  0.33
1     Rest Area  0.33
2  Tennis Court  0.33
3     Multiplex  0.00
4        Museum  0.00


----Maspeth----
               venue  freq
0              Diner  0.09
1      Grocery Store  0.09
2        Pizza Place  0.09
3               Bank  0.06
4  Mobile Phone Shop  0.06


----Middle Village----
           venue  freq
0  Deli / Bodega  0.06
1         Bakery  0.06
2   Dessert Shop  0.06
3     Playground  0.06
4    Pizza Place  0.06


----Murray Hill----
               venue  freq
0  Korean Restaurant  0.49
1               Bank  0.04
2        Coffee Shop  0.04
3        Supermarket  0.04
4                Bar  0.04


----Neponsit----
                  venue  freq
0                 Beach  0.83
1          

### Let's put that into a pandas dataframe

Let's use the function to sort the venues in descending order and let's create the new dataframe and display the top 10 venues for each neighborhood.

In [123]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sortedQueens = pd.DataFrame(columns=columns)
neighborhoods_venues_sortedQueens['Neighborhood'] = queens_grouped['Neighborhood']

for ind in np.arange(queens_grouped.shape[0]):
    neighborhoods_venues_sortedQueens.iloc[ind, 1:] = return_most_common_venues(queens_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sortedQueens.head()

Neighborhood 1st Most Common Venue      2nd Most Common Venue  \
0          Arverne             Surf Spot              Metro Station   
1          Astoria                   Bar  Middle Eastern Restaurant   
2  Astoria Heights            Playground                     Bakery   
3       Auburndale     Mobile Phone Shop              Train Station   
4      Bay Terrace        Clothing Store              Women's Store   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0            Playground            Donut Shop              Bus Stop   
1    Seafood Restaurant                  Café      Greek Restaurant   
2           Bus Station                 Motel           Pizza Place   
3    Miscellaneous Shop    Athletics & Sports    Italian Restaurant   
4        Cosmetics Shop     Mobile Phone Shop                  Bank   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0           Pizza Place                  Café            Board Shop   
1                Bakery            Hookah Bar     Indian Restaurant   
2         Shopping Mall      Business Service         Bowling Alley   
3      Toy / Game Store        Mattress Store        Discount Store   
4            Donut Shop            Kids Store            Shoe Store   

      9th Most Common Venue 10th Most Common Venue  
0                     Beach         Sandwich Place  
1  Mediterranean Restaurant                    Pub  
2               Supermarket           Gourmet Shop  
3               Supermarket              Pet Store  
4       American Restaurant               Pharmacy

### Clustering of the neighborhoods of Queens

Run k-means to cluster the neighborhood into 5 clusters.

In [124]:
# set number of clusters
kclusters = 5

queens_grouped_clustering = queens_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(queens_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1])

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [125]:
# add clustering labels
neighborhoods_venues_sortedQueens.insert(0, 'Cluster Labels', kmeans.labels_)

queens_merged = queendf

# merge queens_merged with queensdf to add latitude/longitude for each neighborhood
queens_merged = queens_merged.join(neighborhoods_venues_sortedQueens.set_index('Neighborhood'), on='Name')

queens_merged.head() # check the last columns!

Name   Latitude  Longitude  Cluster Labels  \
0  Queensboro Hill  40.744572 -73.825809               1   
1       Somerville  40.597711 -73.796648               0   
2    Rockaway Park  40.580343 -73.841534               1   
3     Belle Harbor  40.576156 -73.854018               1   
4      Lefrak City  40.736075 -73.862525               1   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0    Chinese Restaurant                  Bank                Bakery   
1                  Park         Women's Store  Fast Food Restaurant   
2                 Beach           Pizza Place            Donut Shop   
3                 Beach         Deli / Bodega                   Spa   
4        Cosmetics Shop         Women's Store                Bakery   

  4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
0            Playground      Asian Restaurant                  Café   
1         Event Service           Event Space    Falafel Restaurant   
2        Ice Cream Shop            Bagel Shop              Pharmacy   
3                   Pub    Mexican Restaurant                Bakery   
4       Bubble Tea Shop    Mexican Restaurant   Fried Chicken Joint   

  7th Most Common Venue    8th Most Common Venue   9th Most Common Venue  \
0           Pizza Place       Frozen Yogurt Shop             Supermarket   
1                  Farm           Farmers Market     Filipino Restaurant   
2                 Diner           Sandwich Place      Seafood Restaurant   
3            Bagel Shop               Restaurant                Boutique   
4                   Spa  Fruit & Vegetable Store  Furniture / Home Store   

  10th Most Common Venue  
0                    Bar  
1      Electronics Store  
2             Smoke Shop  
3             Donut Shop  
4                 Bistro

Let's visualize the resulting clusters

In [126]:
# create map
map_clustersQueens = folium.Map(location=[latitudeq, longitudeq], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(queens_merged['Latitude'], queens_merged['Longitude'], queens_merged['Name'], queens_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clustersQueens)
       
map_clustersQueens

## Examine Clusters of Queens

Now, we can examine each cluster and determine the discriminating venue categories that distinguish each cluster.

### Cluster 1

In [127]:
queens_merged.loc[queens_merged['Cluster Labels'] == 0, queens_merged.columns[[0] + list(range(4, queens_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
1  Somerville                  Park         Women's Store   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
1  Fast Food Restaurant         Event Service           Event Space   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
1    Falafel Restaurant                  Farm        Farmers Market   

  9th Most Common Venue 10th Most Common Venue  
1   Filipino Restaurant      Electronics Store

### Cluster 2

In [128]:
queens_merged.loc[queens_merged['Cluster Labels'] == 1, queens_merged.columns[[0] + list(range(4, queens_merged.shape[1]))]]

Name            1st Most Common Venue  \
0        Queensboro Hill               Chinese Restaurant   
2          Rockaway Park                            Beach   
3           Belle Harbor                            Beach   
4            Lefrak City                   Cosmetics Shop   
5             Lindenwood                            Hotel   
6             Ravenswood               Chinese Restaurant   
7              Hillcrest                    Grocery Store   
9               Bellaire               Chinese Restaurant   
10        Middle Village                   Cosmetics Shop   
11  Forest Hills Gardens                             Food   
12         Jamaica Hills                         Pharmacy   
13                Utopia                    Deli / Bodega   
14               Pomonok                       Playground   
15       Astoria Heights                       Playground   
16         Hunters Point                             Café   
17     Sunnyside Gardens                              Bar   
18            Blissville                      Bus Station   
19               Roxbury                    Deli / Bodega   
20       Jamaica Estates                     Intersection   
22          North Corona                    Deli / Bodega   
23            Holliswood                Mobile Phone Shop   
24             Laurelton             Caribbean Restaurant   
25           Murray Hill                Korean Restaurant   
26            Whitestone                    Deli / Bodega   
27               Bayside                              Bar   
28            Auburndale                Mobile Phone Shop   
29           Little Neck                Korean Restaurant   
30            Douglaston                    Deli / Bodega   
31             Glen Oaks                         Pharmacy   
32             Bellerose                    Deli / Bodega   
33     Kew Gardens Hills                             Bank   
34         Fresh Meadows                      Bus Station   
35             Briarwood                       Playground   
36        Jamaica Center                   Clothing Store   
37       Oakland Gardens                Korean Restaurant   
38        Queens Village                             Bank   
39           Floral Park                    Grocery Store   
40                Hollis                Mobile Phone Shop   
41         College Point                           Bakery   
42      South Ozone Park                             Park   
43             Woodhaven                    Deli / Bodega   
44             Rego Park                           Bakery   
45               Astoria                              Bar   
46              Woodside                    Grocery Store   
47       Jackson Heights        Latin American Restaurant   
48              Elmhurst                  Thai Restaurant   
49          Howard Beach                         Pharmacy   
50          South Corona                           Bakery   
51          Forest Hills                              Gym   
52         South Jamaica                           Bakery   
53           Kew Gardens               Chinese Restaurant   
54     Downtown Flushing                  Bubble Tea Shop   
55      Long Island City                            Hotel   
56             Sunnyside                      Pizza Place   
57         East Elmhurst                       Donut Shop   
58               Maspeth                      Pizza Place   
59             Ridgewood                    Grocery Store   
60              Glendale                    Deli / Bodega   
61         Richmond Hill                      Pizza Place   
62            St. Albans             Caribbean Restaurant   
63            Ozone Park                         Pharmacy   
64              Rosedale                      Bus Station   
66              Rochdale  Southern / Soul Food Restaurant   
67   Springfield Gardens                      Bus Station   
68       Cambria Heights             Caribbean Restaura

### Cluster 3

In [129]:
queens_merged.loc[queens_merged['Cluster Labels'] == 2, queens_merged.columns[[0] + list(range(4, queens_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
8  Brookville         Deli / Bodega         Women's Store   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
8     Fish & Chips Shop           Event Space    Falafel Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
8                  Farm        Farmers Market  Fast Food Restaurant   

  9th Most Common Venue 10th Most Common Venue  
8   Filipino Restaurant            Fish Market

### Cluster 4

In [130]:
queens_merged.loc[queens_merged['Cluster Labels'] == 3, queens_merged.columns[[0] + list(range(4, queens_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
21  Malba             Rock Club             Rest Area          Tennis Court   

   4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
21         Women's Store     Electronics Store   Empanada Restaurant   

   7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
21         Event Service           Event Space    Falafel Restaurant   

   10th Most Common Venue  
21                   Farm

### Cluster 5

In [131]:
queens_merged.loc[queens_merged['Cluster Labels'] == 4, queens_merged.columns[[0] + list(range(4, queens_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
65      Neponsit                 Beach             Beach Bar   
74  Breezy Point                 Beach   Monument / Landmark   

   3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
65         Women's Store   Filipino Restaurant    Falafel Restaurant   
74              Bus Stop                 Trail   Filipino Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
65                  Farm        Farmers Market  Fast Food Restaurant   
74    Falafel Restaurant                  Farm        Farmers Market   

   9th Most Common Venue 10th Most Common Venue  
65     Fish & Chips Shop             Food Truck  
74  Fast Food Restaurant          Women's Store

In the Queens cluster have a cluster that is more common that the other ones, In this specific cluster that is the number 5 in our k-means procedure, we can see that most of this venues donuts shops, some Chinese restaurants and deli or bodegas, there are other similitudes but most neighborhoods in Queens have this characteristics.

We can finally visualize the cluster of neighborhoods in Queens, lets finally go with Staten Island


## Explore Neighborhoods in Staten Island

In [133]:
staten_venues = getNearbyVenues(names=statisdf['Name'],
                                   latitudes=statisdf['Latitude'],
                                   longitudes=statisdf['Longitude'],
                              )

Grymes Hill
Todt Hill
South Beach
Port Richmond
Mariner's Harbor
Port Ivory
Castleton Corners
New Springville
West Brighton
Rosebank
Silver Lake
New Brighton
St. George
Travis
Manor Heights
Willowbrook
Sandy Ground
Egbertville
Prince's Bay
Lighthouse Hill
Richmond Valley
Stapleton
New Dorp
Elm Park
Howland Hook
Huguenot
Bay Terrace
New Dorp Beach
Grant City
Midland Beach
Dongan Hills
Old Town
Grasmere
Arrochar
Arlington
Graniteville
Westerleigh
Park Hill
Tottenville
Tompkinsville
Pleasant Plains
Butler Manor
Woodrow
Rossville
Randall Manor
Emerson Hill
Concord
Clifton
Shore Acres
Richmond Town
Oakwood
Sunnyside
Great Kills
Annadale
Bulls Head
Bloomfield
Chelsea
Heartland Village
Greenridge
Arden Heights
Eltingville
Charleston


Let's check the size of the resulting dataframe

In [134]:
print(staten_venues.shape)
staten_venues.head()

(816, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  Grymes Hill              40.624185              -74.087248   
1  Grymes Hill              40.624185              -74.087248   
2  Grymes Hill              40.624185              -74.087248   
3    Todt Hill              40.597069              -74.111329   
4  South Beach              40.580247              -74.079553   

                             Venue  Venue Latitude  Venue Longitude  \
0         Silver Lake Park Dog Run       40.626393       -74.091626   
1          Island Food Market Inc.       40.623856       -74.082571   
2                            Zumba       40.624850       -74.081725   
3             St Francis Woodlands       40.599524       -74.114515   
4  Franklin D. Roosevelt Boardwalk       40.579832       -74.076147   

  Venue Category  
0        Dog Run  
1  Deli / Bodega  
2            Gym  
3           Park  
4          Beach

In [135]:
staten_venues.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                              
Annadale                              10                      10     10   
Arden Heights                          4                       4      4   
Arlington                              4                       4      4   
Arrochar                              22                      22     22   
Bay Terrace                           10                      10     10   
Bloomfield                             4                       4      4   
Bulls Head                            47                      47     47   
Butler Manor                           6                       6      6   
Castleton Corners                     14                      14     14   
Charleston                            26                      26     26   
Chelsea                                7                       7      7   
Clifton                               19                      19     19   
Concord                                8                       8      8   
Dongan Hills                          22                      22     22   
Egbertville                            4                       4      4   
Elm Park                               8                       8      8   
Eltingville                           35                      35     35   
Emerson Hill                           4                       4      4   
Graniteville                           5                       5      5   
Grant City                            22                      22     22   
Grasmere                              26                      26     26   
Great Kills                           24                      24     24   
Greenridge                             9                       9      9   
Grymes Hill                            3                       3      3   
Heartland Village                     13                      13     13   
Howland Hook                           1                       1      1   
Huguenot                               8                       8      8   
Lighthouse Hill                        5                       5      5   
Manor Heights                         12                      12     12   
Mariner's Harbor                       7                       7      7   
Midland Beach                         12                      12     12   
New Brighton                          11                      11     11   
New Dorp                              26                      26     26   
New Dorp Beach                        14                      14     14   
New Springville                       22                      22     22   
Oakwood                                4                       4      4   
Old Town                              19                      19     19   
Park Hill                              6                       6      6   
Pleasant Plains                       16                      16     16   
Port Ivory                             1                       1      1   
Port Richmond                          6                       6      6   
Prince's Bay                          10                      10     10   
Randall Manor                          2                       2      2   
Richmond Town                          4                       4      4   
Richmond Valley                       11                      11     11   
Rosebank                              30                      30     30   
Rossville                             16                      16     16   
Sandy Ground                          12                      12     12   
Shore Acres                           25                      25     25   
Silver Lake                            4                       4      4   
South Beach                            6                       6      6   
St. George                            34    

Let's find out how many unique categories can be curated from all the returned venues

In [136]:
print('There are {} uniques categories.'.format(len(staten_venues['Venue Category'].unique())))

There are 184 uniques categories.


## Analyze Each Neighborhood of Staten Island

In [137]:
staten_onehot = pd.get_dummies(staten_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
staten_onehot['Neighborhood'] = staten_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [staten_onehot.columns[-1]] + list(staten_onehot.columns[:-1])
staten_onehot = staten_onehot[fixed_columns]

staten_onehot.head()

Yoga Studio  ATM  Accessories Store  American Restaurant  Arcade  \
0            0    0                  0                    0       0   
1            0    0                  0                    0       0   
2            0    0                  0                    0       0   
3            0    0                  0                    0       0   
4            0    0                  0                    0       0   

   Art Gallery  Art Museum  Arts & Crafts Store  Asian Restaurant  \
0            0           0                    0                 0   
1            0           0                    0                 0   
2            0           0                    0                 0   
3            0           0                    0                 0   
4            0           0                    0                 0   

   Athletics & Sports  BBQ Joint  Bagel Shop  Bakery  Bank  Bar  \
0                   0          0           0       0     0    0   
1                   0          0           0       0     0    0   
2                   0          0           0       0     0    0   
3                   0          0           0       0     0    0   
4                   0          0           0       0     0    0   

   Baseball Field  Baseball Stadium  Basketball Court  Beach  Beer Bar  \
0               0                 0                 0      0         0   
1               0                 0                 0      0         0   
2               0                 0                 0      0         0   
3               0                 0                 0      0         0   
4               0                 0                 0      1         0   

   Big Box Store  Board Shop  Boat or Ferry  Bookstore  Bowling Alley  \
0              0           0              0          0              0   
1              0           0              0          0              0   
2              0           0              0          0              0   
3              0           0              0          0              0   
4              0           0              0          0              0   

   Breakfast Spot  Brewery  Bubble Tea Shop  Burger Joint  Bus Station  \
0               0        0                0             0            0   
1               0        0                0             0            0   
2               0        0                0             0            0   
3               0        0                0             0            0   
4               0        0                0             0            0   

   Bus Stop  Business Service  Cafeteria  Café  Cajun / Creole Restaurant  \
0         0                 0          0     0                          0   
1         0                 0          0     0                          0   
2         0                 0          0     0                          0   
3         0                 0          0     0                          0   
4         0                 0          0     0                          0   

   Campground  Caribbean Restaurant  Chinese Restaurant  Clothing Store  \
0           0                     0                   0               0   
1           0                     0                   0               0   
2           0                     0                   0               0   
3           0                     0                   0               0   
4           0                     0                   0               0   

   Coffee Shop  Comedy Club  Comfort Food Restaurant  Concert Hall  \
0            0            0                        0             0   
1            0            0                        0             0   
2            0            0                        0             0   
3            0            0                        0             0   
4            0            0                        0             0   

   Construction & Landscaping  Convenience Store  Cosmetics Shop  \
0                         

And let's examine the new dataframe size.

In [138]:
staten_onehot.shape

(816, 184)

### Next, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [139]:
staten_grouped = staten_onehot.groupby('Neighborhood').mean().reset_index()
staten_grouped

Neighborhood  Yoga Studio       ATM  Accessories Store  \
0            Annadale       0.0000  0.000000           0.000000   
1       Arden Heights       0.0000  0.000000           0.000000   
2           Arlington       0.0000  0.000000           0.000000   
3            Arrochar       0.0000  0.000000           0.000000   
4         Bay Terrace       0.0000  0.000000           0.000000   
5          Bloomfield       0.0000  0.000000           0.000000   
6          Bulls Head       0.0000  0.000000           0.000000   
7        Butler Manor       0.0000  0.000000           0.000000   
8   Castleton Corners       0.0000  0.000000           0.000000   
9          Charleston       0.0000  0.000000           0.000000   
10            Chelsea       0.0000  0.000000           0.000000   
11            Clifton       0.0000  0.000000           0.000000   
12            Concord       0.0000  0.000000           0.000000   
13       Dongan Hills       0.0000  0.000000           0.000000   
14        Egbertville       0.0000  0.000000           0.000000   
15           Elm Park       0.0000  0.000000           0.000000   
16        Eltingville       0.0000  0.000000           0.000000   
17       Emerson Hill       0.0000  0.000000           0.000000   
18       Graniteville       0.0000  0.000000           0.000000   
19         Grant City       0.0000  0.000000           0.000000   
20           Grasmere       0.0000  0.000000           0.000000   
21        Great Kills       0.0000  0.000000           0.000000   
22         Greenridge       0.0000  0.000000           0.000000   
23        Grymes Hill       0.0000  0.000000           0.000000   
24  Heartland Village       0.0000  0.000000           0.076923   
25       Howland Hook       0.0000  0.000000           0.000000   
26           Huguenot       0.0000  0.000000           0.000000   
27    Lighthouse Hill       0.0000  0.000000           0.000000   
28      Manor Heights       0.0000  0.000000           0.000000   
29   Mariner's Harbor       0.0000  0.000000           0.000000   
30      Midland Beach       0.0000  0.000000           0.000000   
31       New Brighton       0.0000  0.000000           0.000000   
32           New Dorp       0.0000  0.000000           0.000000   
33     New Dorp Beach       0.0000  0.000000           0.000000   
34    New Springville       0.0000  0.000000           0.045455   
35            Oakwood       0.0000  0.000000           0.000000   
36           Old Town       0.0000  0.000000           0.000000   
37          Park Hill       0.0000  0.000000           0.000000   
38    Pleasant Plains       0.0625  0.000000           0.000000   
39         Port Ivory       0.0000  0.000000           0.000000   
40      Port Richmond       0.0000  0.000000           0.000000   
41       Prince's Bay       0.0000  0.000000           0.000000   
42      Randall Manor       0.0000  0.000000           0.000000   
43      Richmond Town       0.0000  0.000000           0.000000   
44    Richmond Valley       0.0000  0.000000           0.000000   
45           Rosebank       0.0000  0.000000           0.000000   
46          Rossville       0.0000  0.000000           0.000000   
47       Sandy Ground       0.0000  0.000000           0.000000   
48        Shore Acres       0.0400  0.000000           0.000000   
49        Silver Lake       0.0000  0.000000           0.000000   
50        South Beach       0.0000  0.166667           0.000000   
51         St. George       0.0000  0.000000           0.000000   
52          Stapleton       0.0000  0.000000           0.000000   
53          Sunnyside       0.0000  0.000000           0.000000   
54          Todt Hill       0.0000  0.000000           0.000000   
55      Tompkinsville       0.0000  0.000000           0.000000   
56        Tottenville       0.0000  0.000000           0.000000   
57             Travis       0.0000  0.000000           0.000000   
58      West Brighton       0.0000  0.000000           0

Lets check the size again

In [140]:
staten_grouped.shape

(62, 184)

Let's print each neighborhood along with the top 5 most common venues

In [141]:
num_top_venues = 5

for hood in staten_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = staten_grouped[staten_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Annadale----
                 venue  freq
0          Pizza Place   0.2
1           Restaurant   0.1
2                Diner   0.1
3  American Restaurant   0.1
4         Dance Studio   0.1


----Arden Heights----
         venue  freq
0     Bus Stop  0.25
1  Coffee Shop  0.25
2  Pizza Place  0.25
3     Pharmacy  0.25
4  Yoga Studio  0.00


----Arlington----
           venue  freq
0   Intersection  0.25
1       Bus Stop  0.25
2    Coffee Shop  0.25
3  Deli / Bodega  0.25
4      Juice Bar  0.00


----Arrochar----
                      venue  freq
0             Deli / Bodega  0.09
1        Italian Restaurant  0.09
2               Pizza Place  0.09
3                  Bus Stop  0.09
4  Mediterranean Restaurant  0.05


----Bay Terrace----
                venue  freq
0         Supermarket   0.2
1       Grocery Store   0.1
2  Italian Restaurant   0.1
3    Insurance Office   0.1
4          Playground   0.1


----Bloomfield----
               venue  freq
0  Recreation Center  0.25
1       Burge

4                 Bar  0.08


----Silver Lake----
                 venue  freq
0  American Restaurant  0.25
1         Burger Joint  0.25
2          Golf Course  0.25
3          Coffee Shop  0.25
4          Yoga Studio  0.00


----South Beach----
                venue  freq
0                Pier  0.33
1       Deli / Bodega  0.17
2                 ATM  0.17
3               Beach  0.17
4  Athletics & Sports  0.17


----St. George----
                 venue  freq
0       Clothing Store  0.21
1   Italian Restaurant  0.06
2  Sporting Goods Shop  0.06
3                  Bar  0.06
4         Burger Joint  0.03


----Stapleton----
            venue  freq
0  Discount Store  0.09
1     Pizza Place  0.09
2  Sandwich Place  0.06
3            Bank  0.06
4  Cosmetics Shop  0.03


----Sunnyside----
                 venue  freq
0              Theater  0.25
1  American Restaurant  0.12
2                  Spa  0.12
3               Market  0.12
4          Coffee Shop  0.12


----Todt Hill----
         venu

## Let's put that into a pandas dataframe

Let's use the function to sort the venues in descending order and let's create the new dataframe and display the top 10 venues for each neighborhood.

In [142]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sortedStaten = pd.DataFrame(columns=columns)
neighborhoods_venues_sortedStaten['Neighborhood'] = staten_grouped['Neighborhood']

for ind in np.arange(staten_grouped.shape[0]):
    neighborhoods_venues_sortedStaten.iloc[ind, 1:] = return_most_common_venues(staten_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sortedStaten.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0       Annadale           Pizza Place                  Food   
1  Arden Heights           Pizza Place           Coffee Shop   
2      Arlington         Deli / Bodega          Intersection   
3       Arrochar         Deli / Bodega              Bus Stop   
4    Bay Terrace           Supermarket    Italian Restaurant   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                   Bar          Dance Studio   American Restaurant   
1              Pharmacy              Bus Stop         Women's Store   
2           Coffee Shop              Bus Stop     Electronics Store   
3           Pizza Place    Italian Restaurant          Liquor Store   
4         Grocery Store            Playground        Shipping Store   

         6th Most Common Venue       7th Most Common Venue  \
0                Train Station                  Restaurant   
1  Eastern European Restaurant         Filipino Restaurant   
2            Fish & Chips Shop  Financial or Legal Service   
3            Polish Restaurant              Cosmetics Shop   
4                   Donut Shop            Insurance Office   

  8th Most Common Venue  9th Most Common Venue 10th Most Common Venue  
0              Pharmacy                  Diner    Filipino Restaurant  
1  Fast Food Restaurant         Farmers Market            Event Space  
2   Filipino Restaurant   Fast Food Restaurant         Farmers Market  
3              Pharmacy  Outdoors & Recreation         Sandwich Place  
4    Salon / Barbershop       Sushi Restaurant            Escape Room

## Clustering of the neighborhoods of Staten Island

Run k-means to cluster the neighborhood into 5 clusters.

In [143]:
# set number of clusters
kclusters = 5

staten_grouped_clustering = staten_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(staten_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([3, 0, 0, 3, 3, 0, 3, 0, 3, 3])

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood

In [145]:
# add clustering labels
neighborhoods_venues_sortedStaten.insert(0, 'Cluster Labels', kmeans.labels_)

staten_merged = statisdf

# merge staten_merged with statisdf to add latitude/longitude for each neighborhood
staten_merged = staten_merged.join(neighborhoods_venues_sortedStaten.set_index('Neighborhood'), on='Name').dropna()
staten_merged['Cluster Labels'] = staten_merged['Cluster Labels'].apply(np.int64) 
staten_merged # check the last columns!

ValueError: cannot insert Cluster Labels, already exists

Let's visualize the resulting clusters

In [147]:
# create map
map_clustersStaten = folium.Map(location=[latitudest, longitudest], zoom_start=11)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(staten_merged['Latitude'], staten_merged['Longitude'], staten_merged['Name'], staten_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clustersStaten)
       
map_clustersStaten

## Examine Clusters of Staten Island

Now, we can examine each cluster and determine the discriminating venue categories that distinguish each cluster.

## Cluster 1

In [148]:
staten_merged.loc[staten_merged['Cluster Labels'] == 0, staten_merged.columns[[0] + list(range(4, staten_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
3      Port Richmond         Deli / Bodega   Rental Car Location   
4   Mariner's Harbor         Deli / Bodega    Italian Restaurant   
11      New Brighton              Bus Stop         Deli / Bodega   
15       Willowbrook              Bus Stop    Chinese Restaurant   
16      Sandy Ground              Bus Stop          Intersection   
23          Elm Park         Deli / Bodega              Bus Stop   
32          Grasmere              Bus Stop            Bagel Shop   
34         Arlington         Deli / Bodega          Intersection   
37         Park Hill              Bus Stop                 Hotel   
38       Tottenville        Cosmetics Shop          Home Service   
41      Butler Manor                  Pool        Baseball Field   
42           Woodrow             Racetrack         Historic Site   
44     Randall Manor              Bus Stop         Women's Store   
55        Bloomfield     Recreation Center              Bus Stop   
56           Chelsea              Bus Stop            Steakhouse   
59     Arden Heights           Pizza Place           Coffee Shop   

   3rd Most Common Venue 4th Most Common Venue       5th Most Common Venue  \
3            Pizza Place              Bus Stop                  Donut Shop   
4               Bus Stop           Supermarket               Women's Store   
11                  Park            Playground              Discount Store   
15                   Spa         Women's Store           Electronics Store   
16             Racetrack            Playground                  Food Truck   
23    Italian Restaurant           Pizza Place              Ice Cream Shop   
32                  Bank        Ice Cream Shop            Basketball Court   
34           Coffee Shop              Bus Stop           Electronics Store   
37           Coffee Shop  Gym / Fitness Center          Athletics & Sports   
38         Deli / Bodega    Italian Restaurant          Mexican Restaurant   
41           Gas Station              Bus Stop               Women's Store   
42          Intersection              Bus Stop        Gym / Fitness Center   
44     Electronics Store     Fish & Chips Shop  Financial or Legal Service   
55          Burger Joint            Theme Park                Dessert Shop   
56    Spanish Restaurant   Arts & Crafts Store                        Park   
59              Pharmacy              Bus Stop               Women's Store   

          6th Most Common Venue        7th Most Common Venue  \
3           Martial Arts School                  Escape Room   
4             Electronics Store   Financial or Legal Service   
11           Chinese Restaurant            Electronics Store   
15   Financial or Legal Service          Filipino Restaurant   
16                         Café               Clothing Store   
23          American Restaurant                Historic Site   
32                  IT Services                Grocery Store   
34            Fish & Chips Shop   Financial or Legal Service   
37            Electronics Store   Financial or Legal Service   
38                     Bus Stop       Thrift / Vintage Store   
41                  Escape Room   Financial or Legal Service   
42                Moving Target            Electronics Store   
44          Filipino Restaurant         Fast Food Restaurant   
55           Dim Sum Restaurant   Financial or Legal Service   
56               Sandwich Place  Eastern European Restaurant   
59  Eastern European Restaurant          Filipino Restaurant   

          8th Most Common Venue       9th Most Common Venue  \
3    Financial or Legal Service         Filipino Restaurant   
4           Filipino Restaurant        Fast Food Restaurant   
11          Filipino Restaurant        Fast Food Restaurant   
15         Fast Food Restaurant              Farmers Market   
16                  Art Gallery               Historic Site   
23  Eastern European Restaurant         Filipino Restaurant   
32

## Cluster 2

In [149]:
staten_merged.loc[staten_merged['Cluster Labels'] == 1, staten_merged.columns[[0] + list(range(4, staten_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
24  Howland Hook       Marine Terminal         Women's Store   

   3rd Most Common Venue       4th Most Common Venue 5th Most Common Venue  \
24     Fish & Chips Shop  Financial or Legal Service   Filipino Restaurant   

   6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
24  Fast Food Restaurant        Farmers Market           Event Space   

   9th Most Common Venue 10th Most Common Venue  
24         Event Service            Escape Room

### Cluster 3

In [150]:
staten_merged.loc[staten_merged['Cluster Labels'] == 2, staten_merged.columns[[0] + list(range(4, staten_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
1  Todt Hill                  Park         Women's Store   

  3rd Most Common Venue       4th Most Common Venue 5th Most Common Venue  \
1     Fish & Chips Shop  Financial or Legal Service   Filipino Restaurant   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
1  Fast Food Restaurant        Farmers Market           Event Space   

  9th Most Common Venue 10th Most Common Venue  
1         Event Service            Escape Room

### Cluster 4

In [151]:
staten_merged.loc[staten_merged['Cluster Labels'] == 3, staten_merged.columns[[0] + list(range(4, staten_merged.shape[1]))]]

Name    1st Most Common Venue       2nd Most Common Venue  \
0         Grymes Hill            Deli / Bodega                     Dog Run   
2         South Beach                     Pier                         ATM   
6   Castleton Corners              Pizza Place              Ice Cream Shop   
7     New Springville  Health & Beauty Service          Chinese Restaurant   
8       West Brighton              Coffee Shop          Italian Restaurant   
9            Rosebank       Mexican Restaurant               Grocery Store   
10        Silver Lake      American Restaurant                Burger Joint   
12         St. George           Clothing Store          Italian Restaurant   
13             Travis                      Gym                       Hotel   
14      Manor Heights             Liquor Store                     Dog Run   
17        Egbertville           Cosmetics Shop          Italian Restaurant   
18       Prince's Bay              Pizza Place              Ice Cream Shop   
19    Lighthouse Hill                      Spa          Italian Restaurant   
20    Richmond Valley                     Bank        Fast Food Restaurant   
21          Stapleton              Pizza Place              Discount Store   
22           New Dorp       Italian Restaurant                 Pizza Place   
25           Huguenot           Ice Cream Shop               Train Station   
26        Bay Terrace              Supermarket          Italian Restaurant   
27     New Dorp Beach       Italian Restaurant               Deli / Bodega   
28         Grant City     Fast Food Restaurant           French Restaurant   
29      Midland Beach            Deli / Bodega                       Beach   
30       Dongan Hills              Pizza Place                    Pharmacy   
31           Old Town       Italian Restaurant              Ice Cream Shop   
33           Arrochar            Deli / Bodega                    Bus Stop   
35       Graniteville            Boat or Ferry                  Food Truck   
36        Westerleigh        Convenience Store                      Arcade   
39      Tompkinsville                  Brewery               Deli / Bodega   
40    Pleasant Plains               Donut Shop                 Pizza Place   
43          Rossville              Pizza Place                  Bagel Shop   
45       Emerson Hill                     Food  Construction & Landscaping   
46            Concord            Deli / Bodega              Cosmetics Shop   
47            Clifton            Train Station               Grocery Store   
48        Shore Acres                 Bus Stop          Italian Restaurant   
49      Richmond Town               Bagel Shop          Italian Restaurant   
50            Oakwood                   Lawyer                Home Service   
51          Sunnyside                  Theater                         Spa   
52        Great Kills                      Bar          Italian Restaurant   
53           Annadale              Pizza Place                        Food   
54         Bulls Head                 Bus Stop                 Pizza Place   
57  Heartland Village             Liquor Store                         Gym   
58         Greenridge       Chinese Restaurant                      Lounge   
60        Eltingville              Pizza Place            Sushi Restaurant   
61         Charleston           Cosmetics Shop                 Coffee Shop   

   3rd Most Common Venue        4th Most Common Venue  \
0                    Gym                Women's Store   
2          Deli / Bodega                        Beach   
6          Grocery Store                     Bus Stop   
7      Mobile Phone Shop                   Hookah Bar   
8            Music Store                          Bar   
9     Italian Restaurant               Ice Cream Shop   
10           Coffee Shop                  Golf Course   
12   Sporting Goods Shop                          Bar   
13         Deli / Bodega                Bowling Alley   
14      Busine

### Cluster 5

In [152]:
staten_merged.loc[staten_merged['Cluster Labels'] == 4, staten_merged.columns[[0] + list(range(4, staten_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
5  Port Ivory      Business Service         Women's Store   

  3rd Most Common Venue 4th Most Common Venue       5th Most Common Venue  \
5     Electronics Store     Fish & Chips Shop  Financial or Legal Service   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
5   Filipino Restaurant  Fast Food Restaurant        Farmers Market   

  9th Most Common Venue 10th Most Common Venue  
5           Event Space          Event Service

In the borough of Staten Island cluster have a cluster that is more common that the other ones, In this specific cluster that is the number 1 in our k-means procedure, we can see that most of this venues coffee shops, some restaurants, mostly Chinese and American ones, there are other similitudes but most neighborhoods in Staten Island have this characteristics.

Now that we have the clustering of each of the neighborhoods in each borough lets do one of all New York

# Explore Neighborhoods in all of New York

In [154]:
frames = [bronx_grouped, brooklyn_grouped, manhattan_grouped, queens_grouped, staten_grouped]

ny_grouped = pd.concat(frames, sort = True)

In [155]:
ny_grouped.head()

ATM  Accessories Store  Adult Boutique  Afghan Restaurant  \
0  NaN                0.0             NaN                NaN   
1  NaN                0.0             NaN                NaN   
2  NaN                0.0             NaN                NaN   
3  NaN                0.0             NaN                NaN   
4  NaN                0.0             NaN                NaN   

   African Restaurant  American Restaurant  Antique Shop    Arcade  \
0                 0.0             0.000000           NaN  0.047619   
1                 0.0             0.000000           NaN  0.000000   
2                 0.0             0.010309           NaN  0.000000   
3                 0.0             0.000000           NaN  0.000000   
4                 0.0             0.037037           NaN  0.000000   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0               0.0                     NaN          0.0         0.0   
1               0.0                     NaN          0.0         0.0   
2               0.0                     NaN          0.0         0.0   
3               0.0                     NaN          0.0         0.0   
4               0.0                     NaN          0.0         0.0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0             0.000000                   NaN               0.0   
1             0.000000                   NaN               0.0   
2             0.000000                   NaN               0.0   
3             0.000000                   NaN               0.0   
4             0.037037                   NaN               0.0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                 0.0         NaN                    NaN                  NaN   
1                 0.0         NaN                    NaN                  NaN   
2                 0.0         NaN                    NaN                  NaN   
3                 0.0         NaN                    NaN                  NaN   
4                 0.0         NaN                    NaN                  NaN   

   Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  \
0            0.0              NaN        0.0         NaN         0.0   
1            0.0              NaN        0.0         NaN         0.0   
2            0.0              NaN        0.0         NaN         0.0   
3            0.0              NaN        0.0         NaN         0.0   
4            0.0              NaN        0.0         NaN         0.0   

     Bakery      Bank       Bar  Baseball Field  Baseball Stadium  \
0  0.000000  0.047619  0.000000        0.047619               NaN   
1  0.000000  0.000000  0.000000        0.028571               NaN   
2  0.051546  0.030928  0.020619        0.000000               NaN   
3  0.000000  0.125000  0.000000        0.000000               NaN   
4  0.000000  0.037037  0.037037        0.037037               NaN   

   Basketball Court  Bath House  Beach  Beach Bar  Beer Bar  Beer Garden  \
0               0.0         NaN    NaN        NaN       0.0          NaN   
1               0.0         NaN    NaN        NaN       0.0          NaN   
2               0.0         NaN    NaN        NaN       0.0          NaN   
3               0.0         NaN    NaN        NaN       0.0          NaN   
4               0.0         NaN    NaN        NaN       0.0          NaN   

   Beer Store  Big Box Store  Bike Rental / Bike Share  Bike Shop  Bike Trail  \
0         NaN            NaN                       NaN        NaN         NaN   
1         NaN            NaN                       NaN        NaN         NaN   
2         NaN            NaN                       NaN        NaN         NaN   
3         NaN            NaN                       NaN        NaN         NaN   
4         NaN            NaN                       NaN        NaN         NaN   

   Bistro  Board Shop  Boat or Ferry  Bookstore  Boutique  Bowling Alley  \
0     NaN   

Let´s fill the NaN values with 0 to work with this data

In [156]:
ny_grouped.fillna(0, inplace = True)

Lets check the size

In [157]:
ny_grouped.shape

(299, 431)

In [158]:
# move neighborhood column to the first column
ny_grouped = ny_grouped[ ['Neighborhood'] + [ col for col in ny_grouped.columns if col != 'Neighborhood' ] ]

In [159]:
ny_grouped.head()

Neighborhood  ATM  Accessories Store  Adult Boutique  Afghan Restaurant  \
0    Baychester  0.0                0.0             0.0                0.0   
1  Bedford Park  0.0                0.0             0.0                0.0   
2       Belmont  0.0                0.0             0.0                0.0   
3   Castle Hill  0.0                0.0             0.0                0.0   
4   City Island  0.0                0.0             0.0                0.0   

   African Restaurant  American Restaurant  Antique Shop    Arcade  \
0                 0.0             0.000000           0.0  0.047619   
1                 0.0             0.000000           0.0  0.000000   
2                 0.0             0.010309           0.0  0.000000   
3                 0.0             0.000000           0.0  0.000000   
4                 0.0             0.037037           0.0  0.000000   

   Arepa Restaurant  Argentinian Restaurant  Art Gallery  Art Museum  \
0               0.0                     0.0          0.0         0.0   
1               0.0                     0.0          0.0         0.0   
2               0.0                     0.0          0.0         0.0   
3               0.0                     0.0          0.0         0.0   
4               0.0                     0.0          0.0         0.0   

   Arts & Crafts Store  Arts & Entertainment  Asian Restaurant  \
0             0.000000                   0.0               0.0   
1             0.000000                   0.0               0.0   
2             0.000000                   0.0               0.0   
3             0.000000                   0.0               0.0   
4             0.037037                   0.0               0.0   

   Athletics & Sports  Auditorium  Australian Restaurant  Austrian Restaurant  \
0                 0.0         0.0                    0.0                  0.0   
1                 0.0         0.0                    0.0                  0.0   
2                 0.0         0.0                    0.0                  0.0   
3                 0.0         0.0                    0.0                  0.0   
4                 0.0         0.0                    0.0                  0.0   

   Auto Workshop  Automotive Shop  BBQ Joint  Baby Store  Bagel Shop  \
0            0.0              0.0        0.0         0.0         0.0   
1            0.0              0.0        0.0         0.0         0.0   
2            0.0              0.0        0.0         0.0         0.0   
3            0.0              0.0        0.0         0.0         0.0   
4            0.0              0.0        0.0         0.0         0.0   

     Bakery      Bank       Bar  Baseball Field  Baseball Stadium  \
0  0.000000  0.047619  0.000000        0.047619               0.0   
1  0.000000  0.000000  0.000000        0.028571               0.0   
2  0.051546  0.030928  0.020619        0.000000               0.0   
3  0.000000  0.125000  0.000000        0.000000               0.0   
4  0.000000  0.037037  0.037037        0.037037               0.0   

   Basketball Court  Bath House  Beach  Beach Bar  Beer Bar  Beer Garden  \
0               0.0         0.0    0.0        0.0       0.0          0.0   
1               0.0         0.0    0.0        0.0       0.0          0.0   
2               0.0         0.0    0.0        0.0       0.0          0.0   
3               0.0         0.0    0.0        0.0       0.0          0.0   
4               0.0         0.0    0.0        0.0       0.0          0.0   

   Beer Store  Big Box Store  Bike Rental / Bike Share  Bike Shop  Bike Trail  \
0         0.0            0.0                       0.0        0.0         0.0   
1         0.0            0.0                       0.0        0.0         0.0   
2         0.0            0.0                       0.0        0.0         0.0   
3         0.0            0.0                       0.0        0.0         0.0   
4         0.0            0.0                       0.0        0.0         0.0   

   B

In [160]:
num_top_venues = 5

for hood in ny_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = ny_grouped[ny_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Baychester----
                venue  freq
0          Donut Shop  0.10
1      Sandwich Place  0.05
2  Spanish Restaurant  0.05
3      Baseball Field  0.05
4         Men's Store  0.05


----Bedford Park----
                venue  freq
0  Mexican Restaurant  0.11
1               Diner  0.11
2  Chinese Restaurant  0.11
3         Pizza Place  0.09
4      Sandwich Place  0.06


----Belmont----
                venue  freq
0  Italian Restaurant  0.19
1         Pizza Place  0.09
2       Deli / Bodega  0.07
3              Bakery  0.05
4        Dessert Shop  0.03


----Castle Hill----
                       venue  freq
0                      Diner  0.12
1              Deli / Bodega  0.12
2                Bus Station  0.12
3  Latin American Restaurant  0.12
4                   Pharmacy  0.12


----City Island----
                    venue  freq
0      Seafood Restaurant  0.07
1  Thrift / Vintage Store  0.07
2                    Park  0.07
3           Deli / Bodega  0.04
4           Boat or Fe

4      Playground  0.05


----Wakefield----
            venue  freq
0        Pharmacy  0.22
1    Dessert Shop  0.11
2      Donut Shop  0.11
3  Ice Cream Shop  0.11
4  Sandwich Place  0.11


----West Farms----
           venue  freq
0    Bus Station  0.17
1           Park  0.09
2       Bus Stop  0.09
3    Supermarket  0.04
4  Metro Station  0.04


----Westchester Square----
                  venue  freq
0  Fast Food Restaurant  0.09
1              Pharmacy  0.06
2           Pizza Place  0.06
3    Mexican Restaurant  0.06
4        Sandwich Place  0.06


----Williamsbridge----
                  venue  freq
0  Caribbean Restaurant  0.25
1                   Bar  0.25
2             Nightclub  0.25
3            Soup Place  0.25
4  Pakistani Restaurant  0.00


----Woodlawn----
           venue  freq
0            Pub  0.16
1  Deli / Bodega  0.12
2     Playground  0.08
3    Pizza Place  0.08
4  Grocery Store  0.04


----Bath Beach----
                  venue  freq
0    Chinese Restaurant  0.12
1

            venue  freq
0        Bus Stop  0.18
1            Café  0.18
2  Sandwich Place  0.09
3            Food  0.09
4           Beach  0.09


----Manhattan Terrace----
             venue  freq
0      Pizza Place  0.18
1   Ice Cream Shop  0.09
2       Donut Shop  0.09
3    Deli / Bodega  0.09
4  Organic Grocery  0.05


----Marine Park----
              venue  freq
0  Basketball Court  0.08
1               Gym  0.08
2       Coffee Shop  0.08
3    Baseball Field  0.08
4    Clothing Store  0.08


----Midwood----
            venue  freq
0     Pizza Place  0.33
1   Grocery Store  0.08
2          Bakery  0.08
3        Pharmacy  0.08
4  Ice Cream Shop  0.08


----Mill Basin----
                venue  freq
0  Chinese Restaurant  0.10
1         Pizza Place  0.07
2            Pharmacy  0.05
3        Liquor Store  0.05
4                Bank  0.05


----Mill Island----
               venue  freq
0          Locksmith   0.5
1               Pool   0.5
2                ATM   0.0
3  Paella Restauran

ValueError: Length mismatch: Expected axis has 3 elements, new values have 2 elements

There is a problem with the foursquare API with the neighborhood Chelsea, we can still work but be aware that you will se two Chelsea rows.

###  Let's put that into a pandas dataframe

Let's use the function to sort the venues in descending order and let's create the new dataframe and display the top 10 venues for each neighborhood.

In [161]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sortedNY = pd.DataFrame(columns=columns)
neighborhoods_venues_sortedNY['Neighborhood'] = ny_grouped['Neighborhood']

for ind in np.arange(ny_grouped.shape[0]):
    neighborhoods_venues_sortedNY.iloc[ind, 1:] = return_most_common_venues(ny_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sortedNY.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0    Baychester            Donut Shop           Men's Store   
1  Bedford Park    Chinese Restaurant                 Diner   
2       Belmont    Italian Restaurant           Pizza Place   
3   Castle Hill         Deli / Bodega                 Diner   
4   City Island    Seafood Restaurant                  Park   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0          Sandwich Place                  Bank        Baseball Field   
1      Mexican Restaurant           Pizza Place         Deli / Bodega   
2           Deli / Bodega                Bakery         Grocery Store   
3             Bus Station              Pharmacy                  Bank   
4  Thrift / Vintage Store    Italian Restaurant          Liquor Store   

  6th Most Common Venue      7th Most Common Venue 8th Most Common Venue  \
0     Electronics Store         Mexican Restaurant     Convenience Store   
1        Sandwich Place                 Food Truck         Grocery Store   
2          Dessert Shop                       Bank        Sandwich Place   
3           Pizza Place  Latin American Restaurant                Market   
4    Spanish Restaurant                       Café           Music Venue   

  9th Most Common Venue 10th Most Common Venue  
0           Supermarket         Cosmetics Shop  
1           Supermarket    Fried Chicken Joint  
2    Mexican Restaurant     Spanish Restaurant  
3           Film Studio            Fish Market  
4            Smoke Shop          Boat or Ferry

### Clustering of the neighborhoods of New York

Run k-means to cluster the neighborhood into 5 clusters.

In [162]:
# set number of clusters, set more clusters to see more diference.
kclusters = 8

ny_grouped_clustering = ny_grouped.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(ny_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10]

array([2, 2, 4, 2, 4, 2, 4, 2, 2, 2])

Let's create a new dataframe that includes the cluster as well as the top 10 venues for each neighborhood.

In [163]:
neighborhoods_venues_sortedNY.shape

(299, 11)

In [164]:
# add clustering labels
neighborhoods_venues_sortedNY.insert(0, 'Cluster Labels', kmeans.labels_)

ny_merged = nydf

# merge ny_merged with nydf to add latitude/longitude for each neighborhood
ny_merged = ny_merged.join(neighborhoods_venues_sortedNY.set_index('Neighborhood'), on='Name').dropna()
ny_merged['Cluster Labels'] = ny_merged['Cluster Labels'].apply(np.int64) #There was a problem with the join function with a neightborhood name that didnt have values so use this to drop and put everything to int again.
ny_merged # check the last columns!

Borough                       Name   Latitude  Longitude  \
0            Bronx                  Wakefield  40.894705 -73.847201   
1            Bronx               Clason Point  40.806551 -73.854144   
2            Bronx                Throgs Neck  40.815109 -73.816350   
3            Bronx               Country Club  40.844246 -73.824099   
4            Bronx                Parkchester  40.837938 -73.856003   
5            Bronx         Westchester Square  40.840619 -73.842194   
6            Bronx                   Van Nest  40.843608 -73.866299   
7            Bronx                Morris Park  40.847549 -73.850402   
8            Bronx                    Belmont  40.857277 -73.888452   
9            Bronx             Spuyten Duyvil  40.881395 -73.917190   
10           Bronx            North Riverdale  40.908543 -73.904531   
11           Bronx                  Soundview  40.821012 -73.865746   
12           Bronx                 Pelham Bay  40.850641 -73.832074   
13           Bronx             Edgewater Park  40.821986 -73.813885   
14           Bronx                  Olinville  40.871371 -73.863324   
15           Bronx             Pelham Gardens  40.862966 -73.841612   
16           Bronx                  Concourse  40.834284 -73.915589   
17           Bronx                  Unionport  40.829774 -73.850535   
18           Bronx                   Edenwald  40.884561 -73.848083   
19           Bronx                 Mount Hope  40.848842 -73.908299   
20           Bronx                 Mount Eden  40.843826 -73.916556   
21           Bronx          Concourse Village  40.824780 -73.915847   
22           Bronx          Claremont Village  40.831428 -73.901199   
23           Bronx              Schuylerville  40.826580 -73.826203   
24           Bronx                 Morrisania  40.823592 -73.901506   
25           Bronx                Castle Hill  40.819014 -73.848027   
26           Bronx                   Longwood  40.815099 -73.895788   
27           Bronx                 Co-op City  40.874294 -73.829939   
28           Bronx                Hunts Point  40.809730 -73.883315   
29           Bronx                  Fieldston  40.895437 -73.905643   
30           Bronx                  Riverdale  40.890834 -73.912585   
31           Bronx                Kingsbridge  40.881687 -73.902818   
32           Bronx                   Woodlawn  40.898273 -73.867315   
33           Bronx                    Norwood  40.877224 -73.879391   
34           Bronx             Williamsbridge  40.881039 -73.857446   
35           Bronx                 Baychester  40.866858 -73.835798   
36           Bronx             Pelham Parkway  40.857413 -73.854756   
37           Bronx                Eastchester  40.887556 -73.827806   
38           Bronx               Bedford Park  40.870185 -73.885512   
39           Bronx                    Melrose  40.819754 -73.909422   
40           Bronx               High  Bridge  40.836623 -73.926102   
41           Bronx                 Mott Haven  40.806239 -73.916100   
42           Bronx                 West Farms  40.839475 -73.877745   
43           Bronx                City Island  40.847247 -73.786488   
44           Bronx                    Fordham  40.860997 -73.896427   
45           Bronx             Morris Heights  40.847898 -73.919672   
46           Bronx         University Heights  40.855727 -73.910416   
47           Bronx               East Tremont  40.842696 -73.887356   
48           Bronx                Port Morris  40.801664 -73.913221   
49        Brooklyn          East Williamsburg  40.708492 -73.938858   
50        Brooklyn               Spring Creek  40.657139 -73.869988   
51        Brooklyn                 Georgetown  40.623845 -73.916075   
52        Brooklyn        Prospect Park South  40.647009 -73.962613   
53        Brooklyn                    Midwood  40.625596 -73.957595   
54        Brooklyn                 North Side  40.714823 -73.958809   
55        Brooklyn               Be

We can see that there is a repeated Chelsea neighborhood that is surely causing the problem above with the fourquare API.

Let's visualize the resulting clusters

In [165]:
# create map
map_clustersNY = folium.Map(location=[latitude, longitude], zoom_start=10)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(ny_merged['Latitude'], ny_merged['Longitude'], ny_merged['Name'], ny_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clustersNY)
       
map_clustersNY

Like we can see in the map the most comon clusters are the Cluster 2 and Cluster 5. Lets check each of the clusters and analize.

# Examine Clusters of New York

Now, we can examine each cluster and determine the discriminating venue categories that distinguish each cluster.

### Cluster 1

In [166]:
ny_merged.loc[ny_merged['Cluster Labels'] == 0, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
232  Broad Channel         Deli / Bodega                  Park   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
232   Sporting Goods Shop              Dive Bar       Other Nightlife   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
232           Pizza Place           Flea Market        Farmers Market   

    9th Most Common Venue 10th Most Common Venue  
232  Fast Food Restaurant                  Field

### Cluster 2

In [167]:
ny_merged.loc[ny_merged['Cluster Labels'] == 1, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
74   Paerdegat Basin                  Food      Asian Restaurant   
242       Port Ivory      Business Service           Yoga Studio   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
74       Business Service    Child Care Service        Farmers Market   
242                  Food                  Farm        Farmers Market   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
74   Fast Food Restaurant                 Field   Filipino Restaurant   
242  Fast Food Restaurant                 Field   Filipino Restaurant   

    9th Most Common Venue      10th Most Common Venue  
74            Film Studio  Financial or Legal Service  
242           Film Studio  Financial or Legal Service

### Cluster 3

In [168]:
ny_merged.loc[ny_merged['Cluster Labels'] == 2, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Name      1st Most Common Venue  \
0               Wakefield                   Pharmacy   
4             Parkchester                Supermarket   
5      Westchester Square       Fast Food Restaurant   
6                Van Nest              Deli / Bodega   
7             Morris Park                Pizza Place   
9          Spuyten Duyvil                Pizza Place   
10        North Riverdale                Pizza Place   
11              Soundview         Chinese Restaurant   
12             Pelham Bay                       Bank   
14              Olinville       Caribbean Restaurant   
15         Pelham Gardens                Bus Station   
16              Concourse              Grocery Store   
17              Unionport                 Donut Shop   
18               Edenwald              Grocery Store   
19             Mount Hope              Grocery Store   
20             Mount Eden                   Pharmacy   
21      Concourse Village             Sandwich Place   
22      Claremont Village              Grocery Store   
23          Schuylerville         Mexican Restaurant   
24             Morrisania             Discount Store   
25            Castle Hill              Deli / Bodega   
26               Longwood              Grocery Store   
27             Co-op City                Bus Station   
28            Hunts Point                  Juice Bar   
29              Fieldston       Medical Supply Store   
30              Riverdale                       Park   
31            Kingsbridge                Pizza Place   
32               Woodlawn                        Pub   
33                Norwood                Pizza Place   
35             Baychester                 Donut Shop   
36         Pelham Parkway         Italian Restaurant   
37            Eastchester                Bus Station   
38           Bedford Park         Chinese Restaurant   
39                Melrose                Pizza Place   
40           High  Bridge                Pizza Place   
41             Mott Haven                Pizza Place   
42             West Farms                Bus Station   
44                Fordham                 Shoe Store   
45         Morris Heights              Deli / Bodega   
46     University Heights        Fried Chicken Joint   
47           East Tremont                Pizza Place   
50           Spring Creek             Discount Store   
51             Georgetown                       Bank   
52    Prospect Park South       Caribbean Restaurant   
53                Midwood                Pizza Place   
56              City Line                 Donut Shop   
57             Ocean Hill              Deli / Bodega   
64                  Rugby       Caribbean Restaurant   
65          Fort Hamilton                Pizza Place   
67              Homecrest                       Bank   
69      Broadway Junction                 Donut Shop   
70             Weeksville                  Juice Bar   
75               New Lots                Pizza Place   
76         Remsen Village       Caribbean Restaurant   
77                Wingate        Fried Chicken Joint   
78            Ditmas Park         Chinese Restaurant   
79          Highland Park              Grocery Store   
80             Mill Basin         Chinese Restaurant   
81            Marine Park                Coffee Shop   
85            Sunset Park  Latin American Restaurant   
89             Kensington              Grocery Store   
90          East Flatbush         Chinese Restaurant   
91          Crown Heights                Pizza Place   
92               Flatbush                   Pharmacy   
93      Manhattan Terrace                Pizza Place   
98              Gravesend                     Lounge   
100           Brownsville              Moving Target   
103          Borough Park                       Bank   
104            Bath Beach         Chinese Restaurant   
108             Flatlands                   Pharmacy   
109              Canarsie             Shippin

### Cluster 4

In [169]:
ny_merged.loc[ny_merged['Cluster Labels'] == 3, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
143           Chelsea              Bus Stop            Steakhouse   
167        Brookville         Deli / Bodega                  Food   
240     Port Richmond   Rental Car Location            Donut Shop   
241  Mariner's Harbor         Deli / Bodega    Italian Restaurant   
248      New Brighton              Bus Stop         Deli / Bodega   
252       Willowbrook              Bus Stop    Chinese Restaurant   
260          Elm Park         Deli / Bodega              Bus Stop   
266     Midland Beach         Deli / Bodega                 Beach   
269          Grasmere              Bus Stop                  Bank   
271         Arlington         Deli / Bodega           Coffee Shop   
274         Park Hill              Bus Stop  Gym / Fitness Center   
275       Tottenville         Deli / Bodega          Home Service   
281     Randall Manor              Bus Stop           Yoga Studio   
292        Bloomfield     Recreation Center            Theme Park   
293           Chelsea              Bus Stop            Steakhouse   
296     Arden Heights              Pharmacy           Coffee Shop   

      3rd Most Common Venue 4th Most Common Venue  \
143                    Park    Spanish Restaurant   
167                    Farm        Farmers Market   
240                Bus Stop   Martial Arts School   
241                Bus Stop           Supermarket   
248                    Park            Playground   
252                     Spa           Yoga Studio   
260      Italian Restaurant           Pizza Place   
266               Bookstore        Medical Center   
269              Bagel Shop   Japanese Restaurant   
271                Bus Stop          Intersection   
274             Coffee Shop                 Hotel   
275  Thrift / Vintage Store    Mexican Restaurant   
281                    Food                  Farm   
292                Bus Stop          Burger Joint   
293                    Park    Spanish Restaurant   
296                Bus Stop           Pizza Place   

             5th Most Common Venue 6th Most Common Venue  \
143                 Sandwich Place   Arts & Crafts Store   
167           Fast Food Restaurant                 Field   
240                    Pizza Place         Deli / Bodega   
241                    Flower Shop                  Farm   
248                 Discount Store    Chinese Restaurant   
252                    Flea Market                  Farm   
260            American Restaurant        Ice Cream Shop   
266             Chinese Restaurant             Pet Store   
269  Vegetarian / Vegan Restaurant            Nail Salon   
271                    Flower Shop                  Farm   
274             Athletics & Sports           Yoga Studio   
275             Italian Restaurant              Bus Stop   
281                 Farmers Market  Fast Food Restaurant   
292                   Dessert Shop                  Food   
293                 Sandwich Place   Arts & Crafts Store   
296                    Yoga Studio           Fish Market   

    7th Most Common Venue       8th Most Common Venue  \
143           Flea Market                        Farm   
167   Filipino Restaurant                 Film Studio   
240        Discount Store                        Farm   
241        Farmers Market        Fast Food Restaurant   
248        Farmers Market        Fast Food Restaurant   
252        Farmers Market        Fast Food Restaurant   
260   Fried Chicken Joint          Frozen Yogurt Shop   
266            Restaurant              Baseball Field   
269                  Food               Grocery Store   
271        Farmers Market        Fast Food Restaurant   
274        Farmers Market        Fast Food Restaurant   
275        Cosmetics Shop  Financial or Legal Service   
281                 Field         Filipino Restaurant   
292         Design Studio        Fast Food Restaurant   
293           Flea Market                        Farm   
296     

### Cluster 5

In [170]:
ny_merged.loc[ny_merged['Cluster Labels'] == 4, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Name       1st Most Common Venue  \
1                 Clason Point                        Park   
2                  Throgs Neck                   Juice Bar   
3                 Country Club              Sandwich Place   
8                      Belmont          Italian Restaurant   
13              Edgewater Park          Italian Restaurant   
34              Williamsbridge                   Nightclub   
43                 City Island          Seafood Restaurant   
48                 Port Morris      Furniture / Home Store   
49           East Williamsburg                         Bar   
54                  North Side                 Coffee Shop   
55                Bergen Beach             Harbor / Marina   
58   Prospect Lefferts Gardens                      Bakery   
59                 Boerum Hill                 Coffee Shop   
60                    Downtown                 Coffee Shop   
61                    Sea Gate                 Bus Station   
62                  South Side                         Bar   
63                   Navy Yard                 Film Studio   
66                Clinton Hill                 Pizza Place   
68                       Dumbo                      Bakery   
71                Vinegar Hill                  Food Truck   
72               Ocean Parkway            Sushi Restaurant   
73                Fulton Ferry                        Park   
82                     Madison                  Bagel Shop   
83               Dyker Heights  Construction & Landscaping   
84                 Bensonhurst                Dessert Shop   
86                   Bay Ridge          Italian Restaurant   
87                Williamsburg                  Bagel Shop   
88             Windsor Terrace                       Diner   
94              Sheepshead Bay                Dessert Shop   
95                    Bushwick          Mexican Restaurant   
96              Brighton Beach                  Restaurant   
97                  Greenpoint                 Coffee Shop   
99            Prospect Heights                         Bar   
101         Bedford Stuyvesant                 Coffee Shop   
102           Brooklyn Heights               Deli / Bodega   
105               Coney Island            Baseball Stadium   
106            Manhattan Beach                        Café   
107                Mill Island                   Locksmith   
110            Gerritsen Beach                         Bar   
113                 Park Slope                 Coffee Shop   
114                Fort Greene          Italian Restaurant   
115                    Gowanus          Italian Restaurant   
116                   Red Hook          Seafood Restaurant   
117            Carroll Gardens                      Bakery   
118                Cobble Hill                  Playground   
120                   Flatiron         American Restaurant   
121               Civic Center                 Coffee Shop   
122                 Tudor City          Mexican Restaurant   
123                 Turtle Bay                 Coffee Shop   
124               Sutton Place                         Gym   
125              Midtown South           Korean Restaurant   
126                       Noho          Italian Restaurant   
127              Carnegie Hill                 Coffee Shop   
128            Stuyvesant Town                         Bar   
130               West Village          Italian Restaurant   
131                    Clinton          Italian Restaurant   
132            Upper East Side                     Exhibit   
133                East Harlem          Mexican Restaurant   
134             Central Harlem          African Restaurant   
135             Manhattanville          Seafood Restaurant   
136           Roosevelt Island                        Park   
137            Upper West Side                      Bakery   
138             Lincoln Square                       Plaza   
139         Financial District                 Coffee Shop

### Cluster 6

In [171]:
ny_merged.loc[ny_merged['Cluster Labels'] == 5, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
160  Somerville                  Park           Yoga Studio   
238   Todt Hill                  Park           Yoga Studio   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
160               Factory                  Farm        Farmers Market   
238               Factory                  Farm        Farmers Market   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
160  Fast Food Restaurant                 Field   Filipino Restaurant   
238  Fast Food Restaurant                 Field   Filipino Restaurant   

    9th Most Common Venue      10th Most Common Venue  
160           Film Studio  Financial or Legal Service  
238           Film Studio  Financial or Legal Service

### Cluster 7

In [172]:
ny_merged.loc[ny_merged['Cluster Labels'] == 6, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
261  Howland Hook       Marine Terminal           Yoga Studio   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
261           Flower Shop                  Farm        Farmers Market   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
261  Fast Food Restaurant                 Field   Filipino Restaurant   

    9th Most Common Venue      10th Most Common Venue  
261           Film Studio  Financial or Legal Service

### Cluster 8

In [173]:
ny_merged.loc[ny_merged['Cluster Labels'] == 7, ny_merged.columns[[1] + list(range(5, ny_merged.shape[1]))]]

Name 1st Most Common Venue 2nd Most Common Venue  \
224      Neponsit                 Beach             Beach Bar   
233  Breezy Point                 Beach   Monument / Landmark   

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
224           Yoga Studio                  Food  Fast Food Restaurant   
233                 Trail              Bus Stop           Yoga Studio   

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
224                 Field   Filipino Restaurant           Film Studio   
233  Fast Food Restaurant                 Field   Filipino Restaurant   

          9th Most Common Venue      10th Most Common Venue  
224  Financial or Legal Service           Fish & Chips Shop  
233                 Film Studio  Financial or Legal Service

Now that we can see the clustering of the complete city of New York, even with 8 cluster we can see that the one that takes dominance is the cluster number 3, we can see that most of them have as common place restaurants be it American or Italian and pizza places just in the first ten we can’t see a clear pattern.

## Results <a name="results"></a>

With the k-means clustering it was a success in classifying the different neighborhoods in the boroughs. The clusters in each of the borough most of the neighborhoods fall into one of the labels and the others are left like outlier neighborhoods, so if you are looking for a similar neighborhood in the same borough you will likely be in the common cluster and find a similar neighborhood without a problem, for the outliers it will be a tough search. Now analyzing the New York City clustering, the analysis wasn’t as effective as the other clustering. This kind of process won’t be as effective with data that is so broad. Starting with New York having a lot of stores and restaurants repeated in a lot of neighborhoods, it can be hard to look in an analytic way which neighborhoods are different.

## Discussion <a name="discussion"></a>

Finding a clean and organized dataset is of vital importance to have a smooth work, so it’s important to remark the great work of the open data of New York. Having the right tools it’s what makes this work possible. Even if the Foursquare API worked this time, it has some minor problems and it would be best to avoid this kind of situations when doing a work, so it’s better to study which tools you are going to use before working in the code and use another type of venues API if you have access or knowledge of one. 

## Conclusion <a name="conclusion"></a>

I was able to achieve the aim of the project in doing a successful clustering of the boroughs. The city of New York have a lot of different features, this study didn’t include things like urban areas, atmospheres and lifestyle of the people living in it. So even if the neighborhood similitude is of vital importance for this analysis, to improve this study it might be helpful to add more variables that could be helpful to generate more insights.

#### Note:

If you are looking at this notebook from Github and want to see the maps [https://nbviewer.jupyter.org/github/zehpyr/Coursera_Capstone/blob/8b790bb3e427df67d63091480387f2b1a93a9fde/CAPSTONE%20BATTLE%20OF%20NEIGBORHOODS%20FINAL.ipynb](https://nbviewer.jupyter.org/github/zehpyr/Coursera_Capstone/blob/8b790bb3e427df67d63091480387f2b1a93a9fde/CAPSTONE%20BATTLE%20OF%20NEIGBORHOODS%20FINAL.ipynb)